In [2]:
# Masters Thesis willem

import pypsa
import matplotlib.pyplot as plt
from matplotlib import cm
import cartopy.crs as ccrs
import pandas as pd
import numpy as np
import pickle as pkl
from sklearn.preprocessing import MinMaxScaler
import glob
from dtw import *
import itertools

plt.style.use ("bmh")
from pprint import *
import warnings
warnings.filterwarnings('ignore')

import logging
logger = logging.getLogger()
#logger.setLevel(logging.CRITICAL)


    
#from sklearn_extra.cluster import KMedoids

# Display options
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 40)

# Manual objective analysis -> redispatch cost reduction
# ---------------------

# Plot MANUAL objective insights
# --------------

def plot_objective(df_obj, df_obj_day, df_obj_week):
    """
    Function to plot objective analysis insights
    """

    colors = ["royalblue","navy","lightgreen"]

    # Redispatch cost difference per day
    cols = ["redispatch_cost","redispatch_cost_bat"]
    fig, ax  = plt.subplots(figsize = (20, 5))
    ax.set_ylabel('Redispatch cost (€)',  fontsize = 12)
    ax.set_xlabel("Time horizon (day)", fontsize = 12)
    ax = df_obj_day[cols].plot.line(stacked = False, ax = ax, title = "Daily redispatch cost reduction", 
                                       color = colors, legend = True, linewidth = 2, fontsize = 12)
    df_obj_day["delta_rd_cost"].plot.line(stacked = False, ax = ax, title = "Daily redispatch cost reduction", 
                                       color = "lightgreen", legend = True, linewidth = 2.5, fontsize = 12)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Redispatch cost difference per week
    cols = ["redispatch_cost","redispatch_cost_bat"]
    fig, ax1  = plt.subplots(figsize = (20, 5))
    ax1.set_ylabel('Redispatch cost (€)',  fontsize = 12)
    ax1.set_xlabel("Time horizon (week)", fontsize = 12)
    ax1 = df_obj_week[cols].plot.line(stacked = False, ax = ax1, title = "Weekly redispatch cost reduction", 
                                       color = colors, legend = True, linewidth = 2.5, fontsize = 12)
    df_obj_week["delta_rd_cost"].plot.bar(stacked = False, ax = ax1, title = "Weekly redispatch cost reduction", 
                                       color = "lightgreen", legend = True, width = 0.4, fontsize = 12)
    ax1.set_facecolor('white')
    ax1.grid(color = 'lightgrey', linestyle = '-.', linewidth = 1.0)
    ax1.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Relative redispatch cost savings vs absolute savings
    fig, ax2  = plt.subplots(figsize = (20, 5))
    ax2.set_ylabel('Redispatch cost savings (€)',  fontsize = 12)
    ax2.set_xlabel("Time horizon (day)", fontsize = 12)
    ax2 = df_obj_day["delta_rd_cost"].abs().plot.bar(stacked = False, ax = ax2, title = "Daily redispatch cost reduction", 
                                       color = ["lightgreen"], legend = True, fontsize = 12)
    ax2.set_facecolor('white')
    ax2.legend(loc = "upper left")
    ax2.grid(color = 'gainsboro', linestyle = '-.', linewidth = 1.0)
    ax2.set_axisbelow(True)

    # TODO: REMOVE GRAPH OFFSET
    
    ax2_ = ax2.twinx()
    abs(df_obj_day["delta_rd_cost_rel"]).abs().plot.line(ax = ax2_, linewidth = 1.2, 
                                               color = "crimson", legend = True, fontsize = 12)
    ax2_.set_ylabel('Relative redispatch cost savings',  fontsize = 12)
    #ax2_.set_ylim(0,1.0)
    fig.tight_layout()
    plt.show()
    
def plot_objective_rd(df_obj, df_obj_day, df_obj_week):
    """
    Function to plot objective analysis insights
    """

    colors = ["royalblue","navy","lightgreen"]

    # Redispatch cost per 
    fig, ax  = plt.subplots(figsize = (20, 5))
    ax.set_ylabel('Redispatch cost (€)',  fontsize = 12)
    ax.set_xlabel("Time horizon (day)", fontsize = 12)
    ax = df_obj_day["redispatch_cost"].plot.line(stacked = False, ax = ax, title = "Daily redispatch cost reduction", 
                                       color = colors, legend = True, linewidth = 2, fontsize = 12)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Redispatch cost  per week
    fig, ax1  = plt.subplots(figsize = (20, 5))
    ax1.set_ylabel('Redispatch cost (€)',  fontsize = 12)
    ax1.set_xlabel("Time horizon (week)", fontsize = 12)
    ax1 = df_obj_week["redispatch_cost"].plot.line(stacked = False, ax = ax1, title = "Weekly redispatch cost reduction", 
                                       color = colors, legend = True, linewidth = 2.5, fontsize = 12)
    ax1.set_facecolor('white')
    ax1.grid(color = 'lightgrey', linestyle = '-.', linewidth = 1.0)
    ax1.set_axisbelow(True)
    fig.tight_layout()
    plt.show()


def analyze_objective(network_rd, network_rd_bat):
    # Calculate the hourly realized redispatch cost for every generator 
    cols_rd = [column for column in list(network_rd.generators_t.p) if "pos" in column or "neg" in column]
    cols_rd_b = [column for column in list(network_rd_bat.generators_t.p) if "pos" in column or "neg" in column]
    df_rd_p = network_rd.generators_t.p[cols_rd]
    df_rd_p_bat = network_rd_bat.generators_t.p[cols_rd_b]
    
    # positive redispatch cost
    d_marg_cost = pd.Series(network_rd.generators.marginal_cost.values,index=network_rd.generators.index).to_dict()
    df_ramp = df_rd_p[[column for column in list(df_rd_p) if "pos" in column]]
    df_ramp_bat = df_rd_p_bat[[column for column in list(df_rd_p_bat) if "pos" in column]]
    for col in list(df_ramp):
        df_ramp.loc[:,col] = df_ramp[col] * d_marg_cost[col]
        df_ramp_bat.loc[:,col] = df_ramp_bat [col] * d_marg_cost[col]
    df_ramp_cost = df_ramp.copy()
    df_ramp_cost_bat = df_ramp_bat.copy()
    df_ramp_cost["sum_ramp_cost"] = df_ramp_cost.sum(axis = 1)
    df_ramp_cost_bat["sum_ramp_cost_bat"] = df_ramp_cost_bat.sum(axis = 1)

    # negative redispatch cost
    df_marginal_cost = network_rd.generators_t.marginal_cost.round(2)
    for col in list(df_marginal_cost):
        if "wind" in col or "solar" in col:
            df_marginal_cost[col] = 0
    
    df_marginal_cost_bat = network_rd_bat.generators_t.marginal_cost.round(2)
    for col in list(df_marginal_cost_bat):
        if "wind" in col or "solar" in col:
            df_marginal_cost_bat[col] = 0
    
    df_curtail = df_rd_p[[column for column in list(df_rd_p) if "neg" in column]]
    df_curtail_bat = df_rd_p_bat[[column for column in list(df_rd_p_bat) if "neg" in column]]
    #
    df_curtail_cost = df_curtail * df_marginal_cost
    df_curtail_cost_bat = df_curtail_bat * df_marginal_cost_bat
    # add sums
    df_curtail_cost["sum_curtailment_cost"] = df_curtail_cost.sum(axis = 1)
    df_curtail_cost_bat["sum_curtailment_cost_bat"] = df_curtail_cost_bat.sum(axis = 1)
    
    # For bat only: Compute redispatch costs for batteries:
#     charger_marg_cost = pd.Series(network_rd.links.marginal_cost.values,index=network_rd.generators.index).to_dict()
#     cols_bat = [column for column in list(network_rd.links_t.p0) if "pos" in column or "neg" in column]
#     df_bat_links_p = 
    
    # df for comparison bat vs. no bat
    df_obj = pd.concat([df_curtail_cost["sum_curtailment_cost"], df_curtail_cost_bat["sum_curtailment_cost_bat"],
                                  df_ramp_cost["sum_ramp_cost"], df_ramp_cost_bat["sum_ramp_cost_bat"]], axis = 1)
    df_obj["redispatch_cost"] = df_obj["sum_curtailment_cost"] + df_obj["sum_ramp_cost"]
    df_obj["redispatch_cost_bat"] = df_obj["sum_curtailment_cost_bat"] + df_obj["sum_ramp_cost_bat"]
    df_obj["delta_ramp_cost"] = df_obj["sum_ramp_cost_bat"] - df_obj["sum_ramp_cost"]
    df_obj["delta_curtailment_cost"] = df_obj["sum_curtailment_cost_bat"].round(2) - \
                                                 df_obj["sum_curtailment_cost"].round(2)
    df_obj["delta_rd_cost"] = df_obj["delta_curtailment_cost"] + df_obj["delta_ramp_cost"]
    df_obj["delta_rd_cost_rel"] = df_obj["delta_rd_cost"] / df_obj["redispatch_cost"]
    obj_year = df_obj["redispatch_cost"].sum()
    obj_year_bat = df_obj["redispatch_cost_bat"].sum()
    
    # create dataframe for DAILY redispatch 
    df_obj_day = df_obj.iloc[:,:-1].groupby(np.arange(len(df_obj))//24).sum()
    df_obj_day["delta_rd_cost_rel"] = df_obj_day["delta_rd_cost"] / df_obj_day["redispatch_cost"]

    df_obj_day.index.rename("Time horizon (day)", inplace = True)
    display(df_obj_day)
    # create dataframe for WEEKLY redispatch
    df_obj_week= df_obj_day.groupby(np.arange(len(df_obj_day))//7).sum()[:-1]
    df_obj_week.index.rename("Time horizon (week)", inplace = True)
    print(obj_year)
    print(obj_year_bat)
    
    plot_objective_rd(df_obj, df_obj_day, df_obj_week)


def analyze_objective_rd(network_rd):
    # Calculate the hourly realized redispatch cost for every generator 
    print(network_rd.objective)
    cols_rd = [column for column in list(network_rd.generators_t.p) if "pos" in column or "neg" in column]
    df_rd_p = network_rd.generators_t.p[cols_rd]
    # positive redispatch cost
    d_marg_cost = pd.Series(network_rd.generators.marginal_cost.values,index=network_rd.generators.index).to_dict()
    df_ramp = df_rd_p[[column for column in list(df_rd_p) if "pos" in column]]
    for col in list(df_ramp):
        df_ramp.loc[:,col] = df_ramp[col] * d_marg_cost[col]
    df_ramp_cost = df_ramp.copy()
    df_ramp_cost["sum_ramp_cost"] = df_ramp_cost.sum(axis = 1)
    # negative redispatch cost
    df_marginal_cost = network_rd.generators_t.marginal_cost.round(2)
    
    for col in list(df_marginal_cost):
        if "wind" in col or "solar" in col:
            df_marginal_cost[col] = 0
    display(df_marginal_cost)
    
    df_curtail = df_rd_p[[column for column in list(df_rd_p) if "neg" in column]]
    display(df_curtail)
    df_curtail_cost = df_curtail * df_marginal_cost
    # add sums
    df_curtail_cost["sum_curtailment_cost"] = df_curtail_cost.sum(axis = 1)
    # df for comparison between different redispatch networks
    df_obj = pd.concat([df_curtail_cost["sum_curtailment_cost"], df_ramp_cost["sum_ramp_cost"]], axis = 1)
    df_obj["redispatch_cost"] = df_obj["sum_curtailment_cost"] + df_obj["sum_ramp_cost"]
    
    # create dataframe for DAILY redispatch 
    df_obj_day = df_obj.groupby(np.arange(len(df_obj))//24).sum()
    df_obj_day.index.rename("Time horizon (day)", inplace = True)
    # create dataframe for WEEKLY redispatch
    df_obj_week= df_obj_day.groupby(np.arange(len(df_obj_day))//7).sum()[:-1]
    df_obj_week.index.rename("Time horizon (week)", inplace = True)
    obj_year = df_obj.redispatch_cost.sum()
    print(obj_year)
    
    
    
# Reduction of redispatch energy (positive and negative)
# ---------------

def analyze_dynamic_time_warping(network_rd, network_rd_bat, df_obj, df_obj_day):
    """
    Function to analyze total change in redispatch, curtailment, ramp up energy.
    Function to map time series distance between redispatch energy time series and time series of biggest 
    redispatch cost savings -> map correlation.
    """
    # Redispatch power dataframe
    cols_rd = [column for column in list(network_rd.generators_t.p) if "pos" in column or "neg" in column]         
    df_rd_p = network_rd.generators_t.p[cols_rd]
    df_rd_p_bat = network_rd_bat.generators_t.p[cols_rd]
    # sum of positive redispatch
    cols_pos = [column for column in list(df_rd_p) if "pos" in column]
    df_rd_p["Positive redispatch"] = df_rd_p.loc[:,cols_pos].sum(axis = 1)
    df_rd_p_bat["Positive redispatch bat"] = df_rd_p_bat.loc[:,cols_pos].sum(axis = 1)
    # sum of negative redispatch
    cols_neg = [column for column in list(df_rd_p_bat) if "neg" in column]
    df_rd_p["Negative redispatch"] = df_rd_p.loc[:,cols_neg].sum(axis = 1)
    df_rd_p_bat["Negative redispatch bat"] = df_rd_p_bat.loc[:,cols_neg].sum(axis = 1)

    # Difference of redispatch (pos/neg) and total redispatch datarame
    df_bat_nobat = pd.concat([df_rd_p[["Negative redispatch", "Positive redispatch"]], 
                                 df_rd_p_bat[["Negative redispatch bat", "Positive redispatch bat"]]], 
                                axis = 1)

    # differences in redispatch bat vs no bat
    df_bat_nobat = df_bat_nobat.round(2)
    # diff curtailment: old - new => so that + = more curtailment & - = less curtialment
    df_bat_nobat["Difference in curtailment"] = df_bat_nobat.iloc[:,0] - df_bat_nobat.iloc[:,2]
    df_bat_nobat["Difference in ramp-up"] = df_bat_nobat.iloc[:,3] - df_bat_nobat.iloc[:,1]
    df_bat_nobat["Total redispatch"] = abs(df_bat_nobat["Negative redispatch"]) + abs(df_bat_nobat["Positive redispatch"])
    df_bat_nobat["Total redispatch bat"] = abs(df_bat_nobat["Negative redispatch bat"]) + abs(df_bat_nobat["Positive redispatch bat"])
    df_bat_nobat["Total redispatch difference"] = df_bat_nobat["Total redispatch bat"] - df_bat_nobat["Total redispatch"]
    df_bat_nobat.index.rename("Time horizon (hour)", inplace = True)
    df_bat_nobat = df_bat_nobat.append(df_bat_nobat.sum(axis = 0), ignore_index = True)

    # Create daily dataframe 
    df_bat_nobat_day = df_bat_nobat.iloc[:-1].groupby(np.arange(len(df_obj))//24).sum()
    df_bat_nobat_day.index.rename("Time horizon (day)", inplace = True)
    display(df_bat_nobat_day)
    print(df_bat_nobat_day["Difference in curtailment"].sum())

    # Analyze: are the days of most cost reduction also the days of most redispatch power in the no_bat scenario?
    # --------------

    def get_dtw_diff_matrix(cols:list, df_dtw):
        """
        From a list of column names referring to a pandas dataframe with series as columns, compute a distance matrix by computing the 
        DTW distance of all pairwise combinations of series. I take the column names as input so it does reduce the complexity when indexing.
        """
        diff_matrix = {}
        cross = itertools.product(cols, cols)
        for (col1, col2) in cross:
            series1 = df_dtw[col1]
            series2 = df_dtw[col2]
            #print(series1,series2)
            # measure difference dtw
            diff = dtw(series1, 
                       series2, 
                       keep_internals=True, 
                       step_pattern=rabinerJuangStepPattern(2, "c")).normalizedDistance
            diff_matrix[(col1 , col2)] = [diff]
        # convert to pandas dataframe    
        dtw_diff_df = pd.DataFrame(diff_matrix).T.reset_index()\
          .rename(columns = {"level_0":"Delta_obj_day", "level_1":"Total redispatch", 0:"diff"})\
          .pivot_table(index = "Delta_obj_day", columns = "Total redispatch", values = "diff")
        return dtw_diff_df

    # Create dtw dataframe for comparison of redispatch cost savings and total redispatch energy in nobat scenario
    df_dtw = pd.concat([df_bat_nobat_day["Total redispatch"], - df_obj_day["delta_rd_cost"]], axis = 1).round(2)
    df_dtw[df_dtw == -0.0] = 0
    scaler = MinMaxScaler()
    df_dtw[["Total redispatch","delta_rd_cost"]] = scaler.fit_transform(df_dtw[["Total redispatch","delta_rd_cost"]])
    # distance object
    dtw_diff = dtw(df_dtw.iloc[-40:, 0], df_dtw.iloc[-40:, 1], keep_internals=True, 
                   step_pattern=rabinerJuangStepPattern(2, "b"))
    # Distance matrix
    dtw_diff_df = get_dtw_diff_matrix(list(df_dtw), df_dtw)
    display(dtw_diff_df)

    # WHy dynamic time warping? Because dtw can not only identify direct euclidian similarities for every point but also determine wheather
    # two time series have a similar trend (which is just zeitversetzt), e.g. a very high total redispatch in t = T is usually followed by 
    # a large delta_rd_costs every t = T + 2. Euclidian distance would measure no similarity here!
    
    # Plots of objective and redispatch power reduction
# ------------
    colors = ["royalblue","navy"]
    
    # Dynamic time warping distance between cost difference per day (examplary)
    ax = dtw_diff.plot(type="twoway")
    ax = dtw_diff.plot(type="twoway", offset = -0.5)

    # Negative and positive redispatch w/o bat
    cols = ["Negative redispatch","Positive redispatch"]
    fig, ax  = plt.subplots(figsize = (15, 6))
    ax.set_ylabel('Total hourly redispatch (MW)',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_bat_nobat_day[cols].plot.line(stacked = False, ax = ax, title = "Hourly redispatch power comparison", 
                                       color = colors, legend = True, linewidth = 1.2, fontsize = 12)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Negative and positive redispatch WITH bat
    cols = ["Negative redispatch bat","Positive redispatch bat"]
    fig, ax  = plt.subplots(figsize = (15, 6))
    ax.set_ylabel('Total hourly redispatch (MW)',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_bat_nobat_day[cols].plot.line(stacked = False, ax = ax, title = "Hourly redispatch power comparison", 
                                       color = colors, legend = True, linewidth = 1.2, fontsize = 12)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Plot difference in curtailment energy bat vs nobat
    cols = ["Difference in curtailment"]
    fig, ax  = plt.subplots(figsize = (15, 6))
    ax.set_ylabel('Hourly difference in curtailment power (MW)',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_bat_nobat_day[cols].where(df_bat_nobat_day[cols].ge(0), 0)\
                               .plot.line(stacked = False, ax = ax, title = "Difference in curtailment energy", 
                                          color = "red", legend = True, linewidth = 1, fontsize = 12)
    df_bat_nobat_day[cols].where(df_bat_nobat_day[cols].lt(0), 0).plot.line(ax = ax, color = "green", linewidth = 0.8)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()
    
# Map the change in merit order
# ------------------

def plot_merit_order(s_dispatch_p_t, s_merit, s_redispatch_p_t, colorarray=["blue","green"]):
    '''
    Plots merit order curve as step function.
    -----
    Param:
    s_dispatch_p_t: row of aggregated generator dispatch power p dataframe at snapshot t
    s_redispatch_p_t: row of aggregated generator dispatch power p dataframe at snapshot t
    s_merit: series with marginal generator prices
    '''
    if s_dispatch_p_t["oil"].sum() == 0:
        np_x = np.cumsum(s_dispatch_p_t.iloc[:-2].to_numpy())
    else:
        np_x = np.cumsum(s_dispatch_p_t.iloc[:-1].to_numpy())
    
    if s_redispatch_p_t["oil"].sum() == 0:
        np_x2 = np.cumsum(s_redispatch_p_t.iloc[:-2].to_numpy())
    else: 
        np_x2 = np.cumsum(s_redispatch_p_t.iloc[:-1].to_numpy())
    
    if s_dispatch_p_t["oil"].sum() == 0 and s_dispatch_p_t["oil"].sum() == 0:
        np_y = s_merit.iloc[:-2].to_numpy()
    else:
        np_y = s_merit.iloc[:-1].to_numpy()
    
    # Plot merit order of dispatch & redispatch
    fig, ax = plt.subplots(figsize=(10, 5))
    ax.step(np_x, np_y, color = colorarray[0], linewidth = 1.2)
    ax.step(np_x2, np_y, color = colorarray[1], linewidth = 1.2)
    ax.set_ylabel('Marginal generation price (€)',  fontsize = 12)
    ax.set_xlabel("Dispatched power (MW)", fontsize = 12)
    ax.set_title("Shift in power plant dispatch from merit order to post-redispatch",  fontsize = 14)
    ax.set_facecolor('white')
    ax.grid(color = 'grey', linestyle = '--', linewidth = 0.5)
    fig.tight_layout()
    plt.show()

def analyze_merit_order_shift(network_d, network_rd, network_rd_bat, df_obj):
    # Generate Merit order per day
    df_gen = network_d.generators.copy()
    dict_prices = df_gen.groupby(["carrier"]).mean()["marginal_cost"].round(4).to_dict()
    dict_prices["offwind"] = dict_prices.pop("offwind-ac")
    dict_prices.pop("offwind-dc")
    for key in dict_prices:
        if dict_prices[key] == 0:
            dict_prices.update({key: 0.01})
    pprint(dict_prices)

    # Create dataframe with dispatch by carrier
    df_dispatch = network_d.generators_t.p.copy()
    cols_CCGT = [column for column in list(df_dispatch) if "CCGT" in column]
    cols_OCGT = [column for column in list(df_dispatch) if "OCGT" in column]
    cols_oil = [column for column in list(df_dispatch) if "oil" in column]
    cols_lignite = [column for column in list(df_dispatch) if "lignite" in column]
    cols_nuclear = [column for column in list(df_dispatch) if "nuclear" in column]
    cols_coal = [column for column in list(df_dispatch) if "coal" in column]
    cols_biomass = [column for column in list(df_dispatch) if "biomass" in column]
    cols_offwind = [column for column in list(df_dispatch) if "offwind" in column]
    cols_onwind = [column for column in list(df_dispatch) if "onwind" in column]
    cols_solar = [column for column in list(df_dispatch) if "solar" in column]
    cols_runofriver = [column for column in list(df_dispatch) if "ror" in column]

    df_dispatch["OCGT"] = df_dispatch[cols_OCGT].sum(axis = 1)
    df_dispatch["CCGT"] = df_dispatch[cols_CCGT].sum(axis = 1)
    df_dispatch["oil"] = df_dispatch[cols_oil].sum(axis = 1)
    df_dispatch["lignite"] = df_dispatch[cols_lignite].sum(axis = 1)
    df_dispatch["nuclear"] = df_dispatch[cols_nuclear].sum(axis = 1)
    df_dispatch["coal"] = df_dispatch[cols_coal].sum(axis = 1)
    df_dispatch["biomass"] = df_dispatch[cols_biomass].sum(axis = 1)
    df_dispatch["offwind"] = df_dispatch[cols_offwind].sum(axis = 1)
    df_dispatch["onwind"] = df_dispatch[cols_onwind].sum(axis = 1)
    df_dispatch["solar"] = df_dispatch[cols_solar].sum(axis = 1)
    df_dispatch["ror"] = df_dispatch[cols_runofriver].sum(axis = 1)
    df_merit = df_dispatch.loc[:,"OCGT":"ror"]

    # Map Marginal prices and sort dataframe for merit order
    df_merit = df_merit.T.round(4)
    df_merit['Marginal price'] = df_merit.index.map(dict_prices)
    df_merit = df_merit.sort_values(by = "Marginal price", axis = 0)
    df_merit = df_merit.T
    # Control sum
    df_merit["sum"] = df_merit.sum(axis = 1)

    # Generate Merit order AFTER REDISPATCH
    df_redis = network_rd.generators_t.p.copy()
    cols_CCGT =    [column for column in list(df_redis) if "CCGT" in column]
    cols_OCGT =    [column for column in list(df_redis) if "OCGT" in column]
    cols_oil =     [column for column in list(df_redis) if "oil" in column]
    cols_lignite = [column for column in list(df_redis) if "lignite" in column]
    cols_nuclear = [column for column in list(df_redis) if "nuclear" in column]
    cols_coal =    [column for column in list(df_redis) if "coal" in column]
    cols_biomass = [column for column in list(df_redis) if "biomass" in column]
    cols_offwind = [column for column in list(df_redis) if "offwind" in column]
    cols_onwind =  [column for column in list(df_redis) if "onwind" in column]
    cols_solar =   [column for column in list(df_redis) if "solar" in column]
    cols_runofriver = [column for column in list(df_redis) if "ror" in column]
    df_redis["OCGT"] =    df_redis[cols_OCGT].sum(axis = 1)
    df_redis["CCGT"] =    df_redis[cols_CCGT].sum(axis = 1)
    df_redis["oil"] =     df_redis[cols_oil].sum(axis = 1)
    df_redis["lignite"] = df_redis[cols_lignite].sum(axis = 1)
    df_redis["nuclear"] = df_redis[cols_nuclear].sum(axis = 1)
    df_redis["coal"] =    df_redis[cols_coal].sum(axis = 1)
    df_redis["biomass"] = df_redis[cols_biomass].sum(axis = 1)
    df_redis["offwind"] = df_redis[cols_offwind].sum(axis = 1)
    df_redis["onwind"] =  df_redis[cols_onwind].sum(axis = 1)
    df_redis["solar"] =   df_redis[cols_solar].sum(axis = 1)
    df_redis["ror"] =     df_redis[cols_runofriver].sum(axis = 1)
    df_merit_rd = df_redis.loc[:,"OCGT":"ror"]
    df_merit_rd = df_merit_rd.T.round(4)
    df_merit_rd['Marginal price'] = df_merit_rd.index.map(dict_prices)
    df_merit_rd = df_merit_rd.sort_values(by = "Marginal price", axis = 0)
    df_merit_rd = df_merit_rd.T
    df_merit_rd["sum"] = df_merit_rd.sum(axis = 1)

    # Generate Merit order AFTER REDISPATCH with BAT
    df_redis_bat = network_rd_bat.generators_t.p.copy()
    cols_CCGT =    [column for column in list(df_redis_bat) if "CCGT" in column]
    cols_OCGT =    [column for column in list(df_redis_bat) if "OCGT" in column]
    cols_oil =     [column for column in list(df_redis_bat) if "oil" in column]
    cols_lignite = [column for column in list(df_redis_bat) if "lignite" in column]
    cols_nuclear = [column for column in list(df_redis_bat) if "nuclear" in column]
    cols_coal =    [column for column in list(df_redis_bat) if "coal" in column]
    cols_biomass = [column for column in list(df_redis_bat) if "biomass" in column]
    cols_offwind = [column for column in list(df_redis_bat) if "offwind" in column]
    cols_onwind =  [column for column in list(df_redis_bat) if "onwind" in column]
    cols_solar =   [column for column in list(df_redis_bat) if "solar" in column]
    cols_runofriver = [column for column in list(df_redis_bat) if "ror" in column]
    df_redis_bat["OCGT"] =    df_redis_bat[cols_OCGT].sum(axis = 1)
    df_redis_bat["CCGT"] =    df_redis_bat[cols_CCGT].sum(axis = 1)
    df_redis_bat["oil"] =     df_redis_bat[cols_oil].sum(axis = 1)
    df_redis_bat["lignite"] = df_redis_bat[cols_lignite].sum(axis = 1)
    df_redis_bat["nuclear"] = df_redis_bat[cols_nuclear].sum(axis = 1)
    df_redis_bat["coal"] =    df_redis_bat[cols_coal].sum(axis = 1)
    df_redis_bat["biomass"] = df_redis_bat[cols_biomass].sum(axis = 1)
    df_redis_bat["offwind"] = df_redis_bat[cols_offwind].sum(axis = 1)
    df_redis_bat["onwind"] =  df_redis_bat[cols_onwind].sum(axis = 1)
    df_redis_bat["solar"] =   df_redis_bat[cols_solar].sum(axis = 1)
    df_redis_bat["ror"] =     df_redis_bat[cols_runofriver].sum(axis = 1)
    df_merit_rd_bat = df_redis_bat.loc[:,"OCGT":"ror"]
    df_merit_rd_bat = df_merit_rd_bat.T.round(4)
    df_merit_rd_bat['Marginal price'] = df_merit_rd_bat.index.map(dict_prices)
    df_merit_rd_bat = df_merit_rd_bat.sort_values(by = "Marginal price", axis = 0)
    df_merit_rd_bat = df_merit_rd_bat.T
    df_merit_rd_bat["sum"] = df_merit_rd_bat.sum(axis = 1)

    # Generate DAILY merit order dataframes
    df_merit_day = df_merit.iloc[:-1].groupby(np.arange(len(df_merit.iloc[:-1]))//24).sum()
    df_merit_rd_day = df_merit_rd.iloc[:-1].groupby(np.arange(len(df_merit_rd.iloc[:-1]))//24).sum()
    df_merit_rd_bat_day = df_merit_rd_bat.iloc[:-1].groupby(np.arange(len(df_merit_rd_bat.iloc[:-1]))//24).sum()

    # METHODOLOGIE: Untersuche den shift der merit order dispatch -> redispatch (bat vs. nobat) an Tagen mit 
    # a) den GRÖSSTEN  Ensparungen an redispatch kosten
    # b) biggest grid loads
    # c) smallest grid loads

    # a) Gather 5 (10) days with biggest redispatch cost savings
    df_obj_l = df_obj.nsmallest(10, "delta_rd_cost")
    l_obj_largest = df_obj_l.index.to_list()
    df_merit_obj = df_merit.loc[l_obj_largest]
    df_merit_rd_obj = df_merit_rd.loc[l_obj_largest]
    df_merit_rd_bat_obj = df_merit_rd_bat.loc[l_obj_largest]

    # b) & c) Gather 5 days with biggest & smallest loads
    df_merit_s = df_merit.iloc[:-1].nsmallest(5, 'sum')
    df_merit_l = df_merit.iloc[:-1].nlargest(5, 'sum')
    l_nlargest = df_merit_l.index.to_list()
    l_nsmallest = df_merit_s.index.to_list()

    # Generate redispatch & rd_bat dataframes with merit order of these days
    df_merit_rd_l = df_merit_rd.loc[l_nlargest]
    df_merit_rd_bat_l = df_merit_rd_bat.loc[l_nlargest]
    
    # series for marginal prices
    s_merit = df_merit.iloc[-1,:]

    # plot hours with largest loads
    for i in range(len(l_nlargest)):
        # plot for with and without bat
        print("\n\n" + str(l_nlargest[i]))
        
        plot_merit_order(df_merit_l.iloc[i,:], s_merit, df_merit_rd_l.iloc[i,:])
        plot_merit_order(df_merit_l.iloc[i,:], s_merit, df_merit_rd_bat_l.iloc[i,:])
        print("taste")
        plot_merit_order(df_merit_rd_l.iloc[i,:], s_merit, df_merit_rd_bat_l.iloc[i,:], colorarray=["red","green"])

    # plot hours with biggest rd cost saving
    for i in range(len(l_obj_largest)):
        plot_merit_order(df_merit_obj.iloc[i,:], s_merit, df_merit_rd_obj.iloc[i,:])
        plot_merit_order(df_merit_obj.iloc[i,:], s_merit, df_merit_rd_bat_obj.iloc[i,:])
        plot_merit_order(df_merit_rd_obj.iloc[i,:], s_merit, df_merit_rd_bat_obj.iloc[i,:], colorarray=["red","green"])

# CO2 ANALYSIS
# ------------

def map_values(row, values_dict):
    if row != "load":
        return values_dict[row]
    else:
        return 0

def analyze_co2_reduction(network_rd,network_rd_bat):
    """
    Function to analyze and plot co2 related metrics
    """

    # W/o bat
    df_gen = network_rd.generators.copy()
    dict_co2 = pd.Series(network_rd.carriers["co2_emissions"].values,index=network_rd.carriers.index).to_dict()
    df_gen["co2_emissions"] = df_gen["carrier"].apply(map_values, args = (dict_co2,)) 
    dict_co2_gen = pd.Series(df_gen["co2_emissions"].values,index=df_gen.index).to_dict()
    cols_rd = [column for column in list(network_rd.generators_t.p) if "pos" in column or "neg" in column]
    df_rd_p = network_rd.generators_t.p[cols_rd].copy()
    # assign co2 emissions to the redispatch energy dataframe
    for col in list(df_rd_p):
        df_rd_p[col] = df_rd_p[col] * dict_co2_gen[col]
    df_rd_p["co2_sum"] = df_rd_p.sum(axis = 1)
    df_rd_p.index.rename("Time horizon (hour)", inplace = True)
    
    # With Bat
    df_gen_bat = network_rd_bat.generators.copy()
    dict_co2 = pd.Series(network_rd_bat.carriers["co2_emissions"].values,index=network_rd_bat.carriers.index).to_dict()
    df_gen_bat["co2_emissions"] = df_gen_bat["carrier"].apply(map_values, args = (dict_co2,))
    dict_co2_gen = pd.Series(df_gen_bat["co2_emissions"].values,index=df_gen_bat.index).to_dict()
    cols_rd = [column for column in list(network_rd_bat.generators_t.p) if "pos" in column or "neg" in column]
    df_rd_p_bat = network_rd_bat.generators_t.p[cols_rd].copy()
    # assign co2 emissions to the redispatch energy dataframe
    for col in list(df_rd_p_bat):
        df_rd_p_bat[col] = df_rd_p_bat[col] * dict_co2_gen[col]
    df_rd_p_bat["co2_sum_bat"] = df_rd_p_bat.sum(axis = 1)
    df_rd_p_bat.index.rename("Time horizon (hour)", inplace = True)

    # Df for direct co2 comparison
    df_co2 = pd.concat([df_rd_p["co2_sum"], df_rd_p_bat["co2_sum_bat"]], axis = 1)
    df_co2["co2_difference"] = df_co2["co2_sum_bat"] - df_co2["co2_sum"]
    df_co2.index.rename("Time horizon (hour)", inplace = True)
    diff_co2_sum = df_co2["co2_difference"].sum()
    
    # Df for daily co2 comparison
    df_co2_day = df_co2.iloc[:-1].groupby(np.arange(len(df_co2.iloc[:-1]))//24).sum()
    co2_sum_day = df_co2_day["co2_difference"].sum()

    display(diff_co2_sum)

    # Wind curtailment analysis -> reduction in wind curtailment
    # -------------
    df_rd_p = network_rd.generators_t.p[cols_rd].copy()
    df_rd_p_bat = network_rd_bat.generators_t.p[cols_rd].copy()
    cols_wind = [column for column in list(df_rd_p) if "wind" in column]
    df_rd_wind = df_rd_p[cols_wind]
    df_rd_bat_wind = df_rd_p_bat[cols_wind]
    df_rd_diff_wind = df_rd_wind - df_rd_bat_wind # > 0 more curtailment < 0 less curtailment
    df_rd_diff_wind["sum_diff_curtailment"] = df_rd_diff_wind.sum(axis = 1)
    # add row with curtailment sums
    df_rd_diff_wind = df_rd_diff_wind.append(df_rd_diff_wind.sum(axis = 0), ignore_index=True)

    # DAILY wind curtailment analysis
    df_rd_diff_wind_day = df_rd_diff_wind.iloc[:-1].groupby(np.arange(len(df_rd_diff_wind.iloc[:-1]))//24).sum()
    df_rd_diff_wind_day.index.rename("Time horizon (day)", inplace = True)

    # WEEKLY wind curtailment analysis
    df_rd_diff_wind_week = df_rd_diff_wind_day.groupby(np.arange(len(df_rd_diff_wind_day))//7).sum()[:-1]
    df_rd_diff_wind_week.index.rename("Time horizon (week)", inplace = True)


    # Conventional analysis -> reduction in conventional ramp up
    # -------------
    df_rd_p = network_rd.generators_t.p[cols_rd].copy()
    df_rd_p_bat = network_rd_bat.generators_t.p[cols_rd].copy()
    cols_pos = [column for column in list(df_rd_p) if "pos" in column]
    df_ramp_p = df_rd_p[cols_pos]
    df_ramp_p_bat = df_rd_p_bat[cols_pos]
    # Only extract columns with conventional carriers 
    cols_gas = [column for column in list(df_ramp_p) if "CCGT" in column or "OCGT" in column]
    cols_oil = [column for column in list(df_ramp_p) if "oil" in column]
    cols_lignite = [column for column in list(df_ramp_p) if "lignite" in column]
    cols_nuclear = [column for column in list(df_ramp_p) if "nuclear" in column]
    cols_coal = [column for column in list(df_ramp_p) if "coal" in column]
    cols_conv = cols_gas + cols_oil + cols_lignite + cols_nuclear + cols_coal + cols_coal
    df_ramp_conv = df_ramp_p[cols_conv]
    df_ramp_conv_bat = df_ramp_p_bat[cols_conv]
    df_ramp_diff_conv = df_ramp_conv_bat - df_ramp_conv # < 0 less ramp up > 0 more ramp up
    df_ramp_diff_conv["sum_diff_ramp_up"] = df_ramp_diff_conv.sum(axis = 1)
    # column for sums of diff per energy carrier
    df_ramp_diff_conv["gas_diff_ramp_up"] = df_ramp_diff_conv[cols_gas].sum(axis = 1)
    df_ramp_diff_conv["oil_diff_ramp_up"] = df_ramp_diff_conv[cols_oil].sum(axis = 1)
    df_ramp_diff_conv["lignite_diff_ramp_up"] = df_ramp_diff_conv[cols_lignite].sum(axis = 1)
    df_ramp_diff_conv["nuclear_diff_ramp_up"] = df_ramp_diff_conv[cols_nuclear].sum(axis = 1)
    df_ramp_diff_conv["coal_diff_ramp_up"] = df_ramp_diff_conv[cols_coal].sum(axis = 1)
    # add row with ramp up sums 
    df_ramp_diff_conv = df_ramp_diff_conv.append(df_ramp_diff_conv.sum(axis = 0), ignore_index=True)

    # DAILY conv ramp up analysis
    df_ramp_diff_conv_day = df_ramp_diff_conv.iloc[:-1].groupby(np.arange(len(df_ramp_diff_conv.iloc[:-1]))//24).sum()
    df_ramp_diff_conv_day.index.rename("Time horizon (day)", inplace = True)

    # WEEKLY conv ramp up analysis
    df_ramp_diff_conv_week = df_ramp_diff_conv_day.groupby(np.arange(len(df_ramp_diff_conv_day))//7).sum()[:-1]
    df_ramp_diff_conv_week.index.rename("Time horizon (week)", inplace = True)

    
    # Plot Co2 insights
    # --------------
    colors = ["navy","green","lightgreen"]

    # CO2 balance with bat vs. w/o bat DAILY
    cols = ["co2_sum","co2_sum_bat"]
    fig, ax  = plt.subplots(figsize = (15, 7))
    ax.set_ylabel('CO2 balance of redispatch',  fontsize = 12)
    ax.set_xlabel("Time horizon (day)", fontsize = 12)
    ax = df_co2_day[cols].plot.line(stacked = False, ax = ax, title = "Hourly Co2 balance of redispatch operations", 
                                       color = colors, legend = True, linewidth = 1.2, fontsize = 12)
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()
    
    # Differences in CO2 balances bat vs. no bat 
    cols = ["co2_difference"]
    fig, ax  = plt.subplots(figsize =(15, 7))
    ax.set_ylabel('CO2 balance of redispatch',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_co2["co2_difference"].where(df_co2["co2_difference"].ge(0), 0).plot.line(stacked = False, ax = ax, title = "Hourly Co2 balance of redispatch operations", 
                                       color = "red", legend = True, linewidth = 1.2, fontsize = 12)
    df_co2["co2_difference"].where(df_co2["co2_difference"].lt(0), 0).plot.line(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()
    
    # Differences in CO2 balances bat vs. no bat DAILY
    cols = ["co2_difference"]
    fig, ax  = plt.subplots(figsize =(15, 7))
    ax.set_ylabel('Difference in CO2 balance of redispatch',  fontsize = 12)
    ax.set_xlabel("Time horizon (day)", fontsize = 12)
    ax = df_co2_day["co2_difference"].where(df_co2_day["co2_difference"].ge(0), 0).plot.line(stacked = False, ax = ax, title = "Daily Co2 balance of redispatch operations", 
                                       color = "red", legend = True, linewidth = 1.2, fontsize = 12)
    df_co2_day["co2_difference"].where(df_co2_day["co2_difference"].lt(0), 0).plot.line(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()


    # Differences in conventional ramp up (without sum row) DAILY
    fig, ax  = plt.subplots(figsize = (15, 7))
    ax.set_ylabel('Difference in conventional ramp up',  fontsize = 12)
    ax.set_xlabel("Time horizon (day)", fontsize = 12)
    ax = df_ramp_diff_conv_day["sum_diff_ramp_up"].where(df_ramp_diff_conv_day["sum_diff_ramp_up"].ge(0), 0)\
    .plot.line(stacked = False, ax = ax, title = "Hourly conventional ramp up", 
               color = "red", legend = True, linewidth = 1.2, fontsize = 12)
    df_ramp_diff_conv_day["sum_diff_ramp_up"].where(df_ramp_diff_conv_day["sum_diff_ramp_up"].lt(0), 0).plot.line(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Differences in conventional ramp up (without sum row) WEEKLY
    fig, ax  = plt.subplots(figsize = (15, 7))
    ax.set_ylabel('Difference in conventional ramp up',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_ramp_diff_conv_week["sum_diff_ramp_up"].where(df_ramp_diff_conv_week["sum_diff_ramp_up"].ge(0), np.NaN)\
    .plot.bar(stacked = False, ax = ax, title = "Weekly conventional ramp up difference", 
               color = "red", legend = True, fontsize = 12)
    df_ramp_diff_conv_week["sum_diff_ramp_up"].where(df_ramp_diff_conv_week["sum_diff_ramp_up"].lt(0), 0).plot.bar(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

    # Wind curtailment

    # Difference in wind curtailment DAILY
    cols = ["sum_diff_curtailment"]
    fig, ax  = plt.subplots(figsize = (15, 7))
    ax.set_ylabel('Difference in wind curtailment',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_rd_diff_wind_day["sum_diff_curtailment"].where(df_rd_diff_wind_day["sum_diff_curtailment"].ge(0), np.NaN)\
                .plot.line(stacked = False, ax = ax, title = "Daily wind curtailment difference", 
                           color = "red", legend = True, linewidth = 1.2, fontsize = 12)
    df_rd_diff_wind_day["sum_diff_curtailment"].where(df_rd_diff_wind_day["sum_diff_curtailment"].lt(0), 0).plot.line(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()
    
    # Difference in wind curtailment WEEKLY
    cols = ["sum_diff_curtailment"]
    fig, ax  = plt.subplots(figsize = (15, 7))
    ax.set_ylabel('Difference in wind curtailment',  fontsize = 12)
    ax.set_xlabel("Time horizon (hour)", fontsize = 12)
    ax = df_rd_diff_wind_week["sum_diff_curtailment"].where(df_rd_diff_wind_week["sum_diff_curtailment"].ge(0), 0)\
                .plot.bar(stacked = False, ax = ax, title = "Weekly wind curtailment difference", 
                           color = "red", legend = True, fontsize = 12)
    df_rd_diff_wind_week["sum_diff_curtailment"].where(df_rd_diff_wind_week["sum_diff_curtailment"].lt(0), 0).plot.bar(ax = ax, color = "green")
    ax.set_facecolor('white')
    ax.grid(color = 'gainsboro', linestyle = '--', linewidth = 1.0)
    ax.set_axisbelow(True)
    fig.tight_layout()
    plt.show()

Importing the dtw module. When using in academic works please cite:
  T. Giorgino. Computing and Visualizing Dynamic Time Warping Alignments in R: The dtw Package.
  J. Stat. Soft., doi:10.18637/jss.v031.i07.



In [18]:
# test networks: 1.09 line cap, jacobs redispatch cost
#n_200_1 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_200_ec_lcopt_1H-noex21_138.nc")
#n_210_1 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_210_ec_lcopt_1H-noex21_138.nc")
#n_220_1 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_220_ec_lcopt_1H-noex21_138.nc")
#n_200_2= pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_200_ec_lcopt_1H-noex22_148.nc")
#n_210_2 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_210_ec_lcopt_1H-noex22_148.nc")
#n_220_2 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\results\redispatch\1 Month test\elec_s300_220_ec_lcopt_1H-noex22_148.nc")

display(n_200_1.generators.groupby("carrier").sum())
display(n_210_1.generators.groupby("carrier").sum())
display(n_220_1.generators.groupby("carrier").sum())
display(n_200_2.generators.groupby("carrier").sum())
display(n_210_2.generators.groupby("carrier").sum())
display(n_220_2.generators.groupby("carrier").sum())


display(n_200_1.objective)
display(n_210_1.objective)
display(n_220_1.objective)
display(n_200_2.objective)
display(n_210_2.objective)
display(n_220_2.objective)


# display(n_200_1.lines)
# display(n_210_1.lines)
# display(n_220_1.lines)
# display(n_200_2.lines)
# display(n_210_2.lines)
# display(n_220_2.lines)

analyze_objective_rd(n_200_1)
analyze_objective_rd(n_210_1)
analyze_objective_rd(n_220_1)
analyze_objective_rd(n_200_2)
analyze_objective_rd(n_210_2)
analyze_objective_rd(n_220_2)

weight         p_nom  efficiency   marginal_cost     p_nom_opt  \
carrier                                                                      
CCGT           0.0  5.436273e+04      75.000     3223.551724  5.436273e+04   
OCGT           0.0  2.413281e+04      86.580     5887.440000  2.413281e+04   
biomass        0.0  1.678040e+03      29.016        0.000000  1.678040e+03   
coal           0.0  5.613876e+04      41.760        0.000000  5.613876e+04   
lignite        0.0  6.250050e+04      24.138      485.640000  6.250050e+04   
load           0.0  1.000000e+07     200.000  1000000.000000  1.000000e+07   
nuclear        0.0  4.736532e+04      11.121       55.000000  4.736532e+04   
offwind-ac     0.0  2.250740e+03      18.000        0.000000  2.250740e+03   
offwind-dc     0.0  6.718140e+03       8.000        0.000000  6.718140e+03   
oil            0.0  1.108920e+04      27.117     2732.170000  1.108920e+04   
onwind         0.0  9.587480e+04     388.000        0.000000  9.587480e+04   
ror            0.0  5.815159e+03     203.400        0.000000  5.815159e+03   
solar          0.0  8.678877e+04     388.000        0.000000  8.678877e+04   

            p_max_pu  p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_set  \
carrier                                                                         
CCGT           100.0                 0        0.0        inf       0.0    0.0   
OCGT           148.0                 0        0.0        inf       0.0    0.0   
biomass         31.0                 0        0.0        inf       0.0    0.0   
coal            45.0                 0        0.0        inf       0.0    0.0   
lignite         36.0                 0        0.0        inf       0.0    0.0   
load           200.0                 0        0.0        inf       0.0    0.0   
nuclear         22.0                 0        0.0        inf       0.0    0.0   
offwind-ac       9.0                 0        0.0        inf       0.0    0.0   
offwind-dc       4.0                 0        0.0        inf       0.0    0.0   
oil             46.0                 0        0.0        inf       0.0    0.0   
onwind         194.0                 0        0.0        inf       0.0    0.0   
ror            113.0                 0        0.0        inf       0.0    0.0   
solar          194.0                 0        0.0        inf       0.0    0.0   

            q_set   sign  capital_cost  committable  start_up_cost  \
carrier                                                              
CCGT          0.0  150.0           0.0            0            0.0   
OCGT          0.0  222.0           0.0            0            0.0   
biomass       0.0   62.0           0.0            0            0.0   
coal          0.0   90.0           0.0            0            0.0   
lignite       0.0   54.0           0.0            0            0.0   
load          0.0  200.0           0.0            0            0.0   
nuclear       0.0   33.0           0.0            0            0.0   
offwind-ac    0.0   18.0           0.0            0            0.0   
offwind-dc    0.0    8.0           0.0            0            0.0   
oil           0.0   69.0           0.0            0            0.0   
onwind        0.0  388.0           0.0            0            0.0   
ror           0.0  226.0           0.0            0            0.0   
solar         0.0  388.0           0.0            0            0.0   

            shut_down_cost  min_up_time  min_down_time  up_time_before  \
carrier                                                                  
CCGT                   0.0            0              0             150   
OCGT                   0.0            0              0             222   
biomass                0.0            0              0              62   
coal                   0.0            0              0              90   
lignite                0.0            0              0              54   
load                   0.0            0              0  

weight         p_nom  marginal_cost  efficiency     p_nom_opt  \
carrier                                                                     
CCGT           0.0  5.436273e+04   3.288023e+03      76.500  5.436273e+04   
OCGT           0.0  2.413281e+04   5.967000e+03      87.750  2.413281e+04   
biomass        0.0  1.678040e+03   0.000000e+00      29.016  1.678040e+03   
coal           0.0  5.613876e+04   0.000000e+00      42.688  5.613876e+04   
lignite        0.0  6.250050e+04   4.856400e+02      24.138  6.250050e+04   
load           0.0  1.050000e+07   1.050000e+06     210.000  1.050000e+07   
nuclear        0.0  4.736532e+04   5.500000e+01      11.121  4.736532e+04   
offwind-ac     0.0  2.250760e+03   0.000000e+00      20.000  2.250760e+03   
offwind-dc     0.0  6.718140e+03   0.000000e+00       8.000  6.718140e+03   
oil            0.0  1.108920e+04   2.732170e+03      27.117  1.108920e+04   
onwind         0.0  9.637492e+04   0.000000e+00     400.000  9.637492e+04   
ror            0.0  5.815159e+03   0.000000e+00     207.000  5.815159e+03   
solar          0.0  8.678889e+04   0.000000e+00     400.000  8.678889e+04   

            p_max_pu  p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_set  \
carrier                                                                         
CCGT           102.0                 0        0.0        inf       0.0    0.0   
OCGT           150.0                 0        0.0        inf       0.0    0.0   
biomass         31.0                 0        0.0        inf       0.0    0.0   
coal            46.0                 0        0.0        inf       0.0    0.0   
lignite         36.0                 0        0.0        inf       0.0    0.0   
load           210.0                 0        0.0        inf       0.0    0.0   
nuclear         22.0                 0        0.0        inf       0.0    0.0   
offwind-ac      10.0                 0        0.0        inf       0.0    0.0   
offwind-dc       4.0                 0        0.0        inf       0.0    0.0   
oil             46.0                 0        0.0        inf       0.0    0.0   
onwind         200.0                 0        0.0        inf       0.0    0.0   
ror            115.0                 0        0.0        inf       0.0    0.0   
solar          200.0                 0        0.0        inf       0.0    0.0   

            q_set   sign  capital_cost  committable  start_up_cost  \
carrier                                                              
CCGT          0.0  153.0           0.0            0            0.0   
OCGT          0.0  225.0           0.0            0            0.0   
biomass       0.0   62.0           0.0            0            0.0   
coal          0.0   92.0           0.0            0            0.0   
lignite       0.0   54.0           0.0            0            0.0   
load          0.0  210.0           0.0            0            0.0   
nuclear       0.0   33.0           0.0            0            0.0   
offwind-ac    0.0   20.0           0.0            0            0.0   
offwind-dc    0.0    8.0           0.0            0            0.0   
oil           0.0   69.0           0.0            0            0.0   
onwind        0.0  400.0           0.0            0            0.0   
ror           0.0  230.0           0.0            0            0.0   
solar         0.0  400.0           0.0            0            0.0   

            shut_down_cost  min_up_time  min_down_time  up_time_before  \
carrier                                                                  
CCGT                   0.0            0              0             153   
OCGT                   0.0            0              0             225   
biomass                0.0            0              0              62   
coal                   0.0            0              0              92   
lignite                0.0            0              0              54   
load                   0.0            0              0             210 

weight         p_nom  marginal_cost  efficiency     p_nom_opt  \
carrier                                                                     
CCGT           0.0  5.436273e+04   3.288023e+03      76.500  5.436273e+04   
OCGT           0.0  2.413281e+04   6.046560e+03      88.920  2.413281e+04   
biomass        0.0  1.678040e+03   0.000000e+00      29.016  1.678040e+03   
coal           0.0  5.613876e+04   0.000000e+00      42.688  5.613876e+04   
lignite        0.0  6.250050e+04   4.586600e+02      22.797  6.250050e+04   
load           0.0  1.100000e+07   1.100000e+06     220.000  1.100000e+07   
nuclear        0.0  4.736532e+04   5.500000e+01      11.121  4.736532e+04   
offwind-ac     0.0  2.250760e+03   0.000000e+00      20.000  2.250760e+03   
offwind-dc     0.0  6.718140e+03   0.000000e+00       8.000  6.718140e+03   
oil            0.0  1.108920e+04   2.732170e+03      27.117  1.108920e+04   
onwind         0.0  9.717504e+04   0.000000e+00     412.000  9.717504e+04   
ror            0.0  5.815159e+03   0.000000e+00     208.800  5.815159e+03   
solar          0.0  8.678903e+04   0.000000e+00     414.000  8.678903e+04   

            p_max_pu  p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_set  \
carrier                                                                         
CCGT           102.0                 0        0.0        inf       0.0    0.0   
OCGT           152.0                 0        0.0        inf       0.0    0.0   
biomass         31.0                 0        0.0        inf       0.0    0.0   
coal            46.0                 0        0.0        inf       0.0    0.0   
lignite         34.0                 0        0.0        inf       0.0    0.0   
load           220.0                 0        0.0        inf       0.0    0.0   
nuclear         22.0                 0        0.0        inf       0.0    0.0   
offwind-ac      10.0                 0        0.0        inf       0.0    0.0   
offwind-dc       4.0                 0        0.0        inf       0.0    0.0   
oil             46.0                 0        0.0        inf       0.0    0.0   
onwind         206.0                 0        0.0        inf       0.0    0.0   
ror            116.0                 0        0.0        inf       0.0    0.0   
solar          207.0                 0        0.0        inf       0.0    0.0   

            q_set   sign  capital_cost  committable  start_up_cost  \
carrier                                                              
CCGT          0.0  153.0           0.0            0            0.0   
OCGT          0.0  228.0           0.0            0            0.0   
biomass       0.0   62.0           0.0            0            0.0   
coal          0.0   92.0           0.0            0            0.0   
lignite       0.0   51.0           0.0            0            0.0   
load          0.0  220.0           0.0            0            0.0   
nuclear       0.0   33.0           0.0            0            0.0   
offwind-ac    0.0   20.0           0.0            0            0.0   
offwind-dc    0.0    8.0           0.0            0            0.0   
oil           0.0   69.0           0.0            0            0.0   
onwind        0.0  412.0           0.0            0            0.0   
ror           0.0  232.0           0.0            0            0.0   
solar         0.0  414.0           0.0            0            0.0   

            shut_down_cost  min_up_time  min_down_time  up_time_before  \
carrier                                                                  
CCGT                   0.0            0              0             153   
OCGT                   0.0            0              0             228   
biomass                0.0            0              0              62   
coal                   0.0            0              0              92   
lignite                0.0            0              0              51   
load                   0.0            0              0             220 

weight         p_nom  efficiency   marginal_cost     p_nom_opt  \
carrier                                                                      
CCGT           0.0  5.436273e+04      75.000     3223.551724  5.436273e+04   
OCGT           0.0  2.413281e+04      86.580     5887.440000  2.413281e+04   
biomass        0.0  1.678040e+03      29.016        0.000000  1.678040e+03   
coal           0.0  5.613876e+04      41.760        0.000000  5.613876e+04   
lignite        0.0  6.250050e+04      24.138      485.640000  6.250050e+04   
load           0.0  1.000000e+07     200.000  1000000.000000  1.000000e+07   
nuclear        0.0  4.736532e+04      11.121       55.000000  4.736532e+04   
offwind-ac     0.0  2.250740e+03      18.000        0.000000  2.250740e+03   
offwind-dc     0.0  6.718140e+03       8.000        0.000000  6.718140e+03   
oil            0.0  1.108920e+04      27.117     2732.170000  1.108920e+04   
onwind         0.0  9.985436e+04     388.000        0.000000  9.985436e+04   
ror            0.0  5.815159e+03     203.400        0.000000  5.815159e+03   
solar          0.0  8.678877e+04     388.000        0.000000  8.678877e+04   

            p_max_pu  p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_set  \
carrier                                                                         
CCGT           100.0                 0        0.0        inf       0.0    0.0   
OCGT           148.0                 0        0.0        inf       0.0    0.0   
biomass         31.0                 0        0.0        inf       0.0    0.0   
coal            45.0                 0        0.0        inf       0.0    0.0   
lignite         36.0                 0        0.0        inf       0.0    0.0   
load           200.0                 0        0.0        inf       0.0    0.0   
nuclear         22.0                 0        0.0        inf       0.0    0.0   
offwind-ac       9.0                 0        0.0        inf       0.0    0.0   
offwind-dc       4.0                 0        0.0        inf       0.0    0.0   
oil             46.0                 0        0.0        inf       0.0    0.0   
onwind         194.0                 0        0.0        inf       0.0    0.0   
ror            113.0                 0        0.0        inf       0.0    0.0   
solar          194.0                 0        0.0        inf       0.0    0.0   

            q_set   sign  capital_cost  committable  start_up_cost  \
carrier                                                              
CCGT          0.0  150.0           0.0            0            0.0   
OCGT          0.0  222.0           0.0            0            0.0   
biomass       0.0   62.0           0.0            0            0.0   
coal          0.0   90.0           0.0            0            0.0   
lignite       0.0   54.0           0.0            0            0.0   
load          0.0  200.0           0.0            0            0.0   
nuclear       0.0   33.0           0.0            0            0.0   
offwind-ac    0.0   18.0           0.0            0            0.0   
offwind-dc    0.0    8.0           0.0            0            0.0   
oil           0.0   69.0           0.0            0            0.0   
onwind        0.0  388.0           0.0            0            0.0   
ror           0.0  226.0           0.0            0            0.0   
solar         0.0  388.0           0.0            0            0.0   

            shut_down_cost  min_up_time  min_down_time  up_time_before  \
carrier                                                                  
CCGT                   0.0            0              0             150   
OCGT                   0.0            0              0             222   
biomass                0.0            0              0              62   
coal                   0.0            0              0              90   
lignite                0.0            0              0              54   
load                   0.0            0              0  

weight         p_nom  marginal_cost  efficiency     p_nom_opt  \
carrier                                                                     
CCGT           0.0  5.436273e+04   3.288023e+03      76.500  5.436273e+04   
OCGT           0.0  2.413281e+04   5.967000e+03      87.750  2.413281e+04   
biomass        0.0  1.678040e+03   0.000000e+00      29.016  1.678040e+03   
coal           0.0  5.613876e+04   0.000000e+00      42.688  5.613876e+04   
lignite        0.0  6.250050e+04   4.856400e+02      24.138  6.250050e+04   
load           0.0  1.050000e+07   1.050000e+06     210.000  1.050000e+07   
nuclear        0.0  4.736532e+04   5.500000e+01      11.121  4.736532e+04   
offwind-ac     0.0  2.250760e+03   0.000000e+00      20.000  2.250760e+03   
offwind-dc     0.0  6.718140e+03   0.000000e+00       8.000  6.718140e+03   
oil            0.0  1.108920e+04   2.732170e+03      27.117  1.108920e+04   
onwind         0.0  1.003545e+05   0.000000e+00     400.000  1.003545e+05   
ror            0.0  5.815159e+03   0.000000e+00     207.000  5.815159e+03   
solar          0.0  8.678889e+04   0.000000e+00     400.000  8.678889e+04   

            p_max_pu  p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_set  \
carrier                                                                         
CCGT           102.0                 0        0.0        inf       0.0    0.0   
OCGT           150.0                 0        0.0        inf       0.0    0.0   
biomass         31.0                 0        0.0        inf       0.0    0.0   
coal            46.0                 0        0.0        inf       0.0    0.0   
lignite         36.0                 0        0.0        inf       0.0    0.0   
load           210.0                 0        0.0        inf       0.0    0.0   
nuclear         22.0                 0        0.0        inf       0.0    0.0   
offwind-ac      10.0                 0        0.0        inf       0.0    0.0   
offwind-dc       4.0                 0        0.0        inf       0.0    0.0   
oil             46.0                 0        0.0        inf       0.0    0.0   
onwind         200.0                 0        0.0        inf       0.0    0.0   
ror            115.0                 0        0.0        inf       0.0    0.0   
solar          200.0                 0        0.0        inf       0.0    0.0   

            q_set   sign  capital_cost  committable  start_up_cost  \
carrier                                                              
CCGT          0.0  153.0           0.0            0            0.0   
OCGT          0.0  225.0           0.0            0            0.0   
biomass       0.0   62.0           0.0            0            0.0   
coal          0.0   92.0           0.0            0            0.0   
lignite       0.0   54.0           0.0            0            0.0   
load          0.0  210.0           0.0            0            0.0   
nuclear       0.0   33.0           0.0            0            0.0   
offwind-ac    0.0   20.0           0.0            0            0.0   
offwind-dc    0.0    8.0           0.0            0            0.0   
oil           0.0   69.0           0.0            0            0.0   
onwind        0.0  400.0           0.0            0            0.0   
ror           0.0  230.0           0.0            0            0.0   
solar         0.0  400.0           0.0            0            0.0   

            shut_down_cost  min_up_time  min_down_time  up_time_before  \
carrier                                                                  
CCGT                   0.0            0              0             153   
OCGT                   0.0            0              0             225   
biomass                0.0            0              0              62   
coal                   0.0            0              0              92   
lignite                0.0            0              0              54   
load                   0.0            0              0             210 

...

name                 DE0 0 CCGT_neg  DE0 0 OCGT_neg  DE0 0 biomass_neg  \
name                                                                     
2018-11-24 00:00:00             0.0             0.0                0.0   
2018-11-24 01:00:00             0.0             0.0                0.0   
2018-11-24 02:00:00             0.0             0.0                0.0   
2018-11-24 03:00:00             0.0             0.0                0.0   
2018-11-24 04:00:00             0.0             0.0                0.0   
...                             ...             ...                ...   
2018-12-31 19:00:00             0.0             0.0                0.0   
2018-12-31 20:00:00             0.0             0.0                0.0   
2018-12-31 21:00:00             0.0             0.0                0.0   
2018-12-31 22:00:00             0.0             0.0                0.0   
2018-12-31 23:00:00             0.0             0.0                0.0   

name                 DE0 0 nuclear_neg  DE0 0 onwind_neg  DE0 0 solar_neg  \
name                                                                        
2018-11-24 00:00:00                0.0               0.0              0.0   
2018-11-24 01:00:00                0.0               0.0              0.0   
2018-11-24 02:00:00                0.0               0.0              0.0   
2018-11-24 03:00:00                0.0               0.0              0.0   
2018-11-24 04:00:00                0.0               0.0              0.0   
...                                ...               ...              ...   
2018-12-31 19:00:00                0.0               0.0              0.0   
2018-12-31 20:00:00                0.0               0.0              0.0   
2018-12-31 21:00:00                0.0               0.0              0.0   
2018-12-31 22:00:00                0.0               0.0              0.0   
2018-12-31 23:00:00                0.0               0.0              0.0   

name                 DE0 1 CCGT_neg  DE0 1 coal_neg  DE0 1 onwind_neg  \
name                                                                    
2018-11-24 00:00:00             0.0             0.0               0.0   
2018-11-24 01:00:00             0.0             0.0               0.0   
2018-11-24 02:00:00             0.0             0.0               0.0   
2018-11-24 03:00:00             0.0             0.0               0.0   
2018-11-24 04:00:00             0.0             0.0               0.0   
...                             ...             ...               ...   
2018-12-31 19:00:00             0.0             0.0               0.0   
2018-12-31 20:00:00             0.0             0.0               0.0   
2018-12-31 21:00:00             0.0             0.0               0.0   
2018-12-31 22:00:00             0.0             0.0               0.0   
2018-12-31 23:00:00             0.0             0.0               0.0   

name                 DE0 1 ror_neg  DE0 1 solar_neg  DE0 10 OCGT_neg  \
name                                                                   
2018-11-24 00:00:00            0.0              0.0              0.0   
2018-11-24 01:00:00            0.0              0.0              0.0   
2018-11-24 02:00:00            0.0              0.0              0.0   
2018-11-24 03:00:00            0.0              0.0              0.0   
2018-11-24 04:00:00            0.0              0.0              0.0   
...                            ...              ...              ...   
2018-12-31 19:00:00            0.0              0.0              0.0   
2018-12-31 20:00:00            0.0              0.0              0.0   
2018-12-31 21:00:00            0.0              0.0              0.0   
2018-12-31 22:00:00            0.0              0.0              0.0   
2018-12-31 23:00:00            0.0              0.0              0.0   

name                 DE0 10 coal_neg  DE0 10 onwind_neg  DE0 10 solar_neg  \
name                                                                   

138677347.4731493
143600147.274025


DE0 0 OCGT_neg  DE0 0 oil_neg  DE0 0 onwind_neg  \
name                                                                   
2018-11-24 00:00:00           36.56          75.79                 0   
2018-11-24 01:00:00           36.56          75.79                 0   
2018-11-24 02:00:00           36.56          75.79                 0   
2018-11-24 03:00:00           36.56          75.79                 0   
2018-11-24 04:00:00           36.56          75.79                 0   
...                             ...            ...               ...   
2018-12-31 19:00:00           47.31          86.54                 0   
2018-12-31 20:00:00           47.31          86.54                 0   
2018-12-31 21:00:00           52.58          91.81                 0   
2018-12-31 22:00:00           52.58          91.81                 0   
2018-12-31 23:00:00           52.58          91.81                 0   

                     DE0 0 ror_neg  DE0 0 solar_neg  DE0 1 OCGT_neg  \
name                                                                  
2018-11-24 00:00:00         -43.00                0           36.56   
2018-11-24 01:00:00         -43.00                0           36.56   
2018-11-24 02:00:00         -43.00                0           36.56   
2018-11-24 03:00:00         -43.00                0           36.56   
2018-11-24 04:00:00         -43.00                0           36.56   
...                            ...              ...             ...   
2018-12-31 19:00:00         -32.25                0           47.31   
2018-12-31 20:00:00         -32.25                0           47.31   
2018-12-31 21:00:00         -26.98                0           52.58   
2018-12-31 22:00:00         -26.98                0           52.58   
2018-12-31 23:00:00         -26.98                0           52.58   

                     DE0 1 lignite_neg  DE0 1 onwind_neg  DE0 1 ror_neg  \
name                                                                      
2018-11-24 00:00:00             -16.02                 0         -43.00   
2018-11-24 01:00:00             -16.02                 0         -43.00   
2018-11-24 02:00:00             -16.02                 0         -43.00   
2018-11-24 03:00:00             -16.02                 0         -43.00   
2018-11-24 04:00:00             -16.02                 0         -43.00   
...                                ...               ...            ...   
2018-12-31 19:00:00              -5.27                 0         -32.25   
2018-12-31 20:00:00              -5.27                 0         -32.25   
2018-12-31 21:00:00               0.00                 0         -26.98   
2018-12-31 22:00:00               0.00                 0         -26.98   
2018-12-31 23:00:00               0.00                 0         -26.98   

                     DE0 1 solar_neg  DE0 10 CCGT_neg  DE0 10 OCGT_neg  \
name                                                                     
2018-11-24 00:00:00                0            21.47            36.56   
2018-11-24 01:00:00                0            21.47            36.56   
2018-11-24 02:00:00                0            21.47            36.56   
2018-11-24 03:00:00                0            21.47            36.56   
2018-11-24 04:00:00                0            21.47            36.56   
...                              ...              ...              ...   
2018-12-31 19:00:00                0            32.22            47.31   
2018-12-31 20:00:00                0            32.22            47.31   
2018-12-31 21:00:00                0            37.49            52.58   
2018-12-31 22:00:00                0            37.49            52.58   
2018-12-31 23:00:00                0            37.49            52.58   

                     DE0 10 lignite_neg  DE0 10 onwind_neg  DE0 10 solar_neg  \
name                                                                           
2018-11-24 00:00:00              -16.02                  0   

name                 DE0 0 OCGT_neg  DE0 0 oil_neg  DE0 0 onwind_neg  \
name                                                                   
2018-11-24 00:00:00             0.0            0.0               0.0   
2018-11-24 01:00:00             0.0            0.0               0.0   
2018-11-24 02:00:00             0.0            0.0               0.0   
2018-11-24 03:00:00             0.0            0.0               0.0   
2018-11-24 04:00:00             0.0            0.0               0.0   
...                             ...            ...               ...   
2018-12-31 19:00:00             0.0            0.0               0.0   
2018-12-31 20:00:00             0.0            0.0               0.0   
2018-12-31 21:00:00             0.0            0.0               0.0   
2018-12-31 22:00:00             0.0            0.0               0.0   
2018-12-31 23:00:00             0.0            0.0               0.0   

name                 DE0 0 ror_neg  DE0 0 solar_neg  DE0 1 OCGT_neg  \
name                                                                  
2018-11-24 00:00:00            0.0              0.0             0.0   
2018-11-24 01:00:00            0.0              0.0             0.0   
2018-11-24 02:00:00            0.0              0.0             0.0   
2018-11-24 03:00:00            0.0              0.0             0.0   
2018-11-24 04:00:00            0.0              0.0             0.0   
...                            ...              ...             ...   
2018-12-31 19:00:00            0.0              0.0             0.0   
2018-12-31 20:00:00            0.0              0.0             0.0   
2018-12-31 21:00:00            0.0              0.0             0.0   
2018-12-31 22:00:00            0.0              0.0             0.0   
2018-12-31 23:00:00            0.0              0.0             0.0   

name                 DE0 1 lignite_neg  DE0 1 onwind_neg  DE0 1 ror_neg  \
name                                                                      
2018-11-24 00:00:00                0.0               0.0            0.0   
2018-11-24 01:00:00                0.0               0.0            0.0   
2018-11-24 02:00:00                0.0               0.0            0.0   
2018-11-24 03:00:00                0.0               0.0            0.0   
2018-11-24 04:00:00                0.0               0.0            0.0   
...                                ...               ...            ...   
2018-12-31 19:00:00                0.0               0.0            0.0   
2018-12-31 20:00:00                0.0               0.0            0.0   
2018-12-31 21:00:00                0.0               0.0            0.0   
2018-12-31 22:00:00                0.0               0.0            0.0   
2018-12-31 23:00:00                0.0               0.0            0.0   

name                 DE0 1 solar_neg  DE0 10 CCGT_neg  DE0 10 OCGT_neg  \
name                                                                     
2018-11-24 00:00:00              0.0              0.0              0.0   
2018-11-24 01:00:00              0.0              0.0              0.0   
2018-11-24 02:00:00              0.0              0.0              0.0   
2018-11-24 03:00:00              0.0              0.0              0.0   
2018-11-24 04:00:00              0.0              0.0              0.0   
...                              ...              ...              ...   
2018-12-31 19:00:00              0.0              0.0              0.0   
2018-12-31 20:00:00              0.0              0.0              0.0   
2018-12-31 21:00:00              0.0              0.0              0.0   
2018-12-31 22:00:00              0.0              0.0              0.0   
2018-12-31 23:00:00              0.0              0.0              0.0   

name                 DE0 10 lignite_neg  DE0 10 onwind_neg  DE0 10 solar_neg  \
name                                                                           
2018-11-24 00:00:00                 0.0 

126550843.70711869


# Build future networks

# Redispatch Workflow: Prepare network for 2025 and 2030

Freiheitsgrade für networks in 2025 und 2030:

1.	Demand side ? (additional load curves by kit)
2.	Nuclear fade out
3.	Start of coal and lignite fade out (most utilized and largest stay): Auch: AUs Netzsicherheitsrechnungen heraus gibt es bedarfe. ÜNB können sagen: Im falle blackout oder fehlerfall, brauchen wir schwarzstartfähige kraftwerke (finden ggf im markt wenig verwendung)  (legitime vereinfachung)
4.	Wind power extensions: Adding 200 MW Generators is capacity is below 200 MW, then adding the remaining generator capacity proportionally to existing ones
5.  Solar power extensions
6.  Biomass extension
7.	Natural Gas extension (Steigerung erdgas): Adding 50 MW Generators is capacity is below 50 MW, then adding the remaining generator capacity proportionally to existing ones
8.  PHS extension (erweiterung waldeck: Streckenmaßnahme M353: Borken – Twistetal Die Maßnahme M353 wird bestätigt. Beschreibung: Im Rahmen der Maßnahme ist die Verstärkung der bestehenden 380-kV-Leitung zwischen Borken und Twistetal durch eine neue 380-kV-Leitung mit einer Stromtragfähigkeit von 4.000A vorgesehen (Netzverstärkung). Außerdem sind die Schaltanlagen in Borken und Twistetal zu verstärken (Netzverstärkung). Weiterhin ist die Schaltanlage in Waldeck voll einzuschleifen. In Waldeck ist außerdem eine Erweiterung des Pumpspeicherkraftwerks geplant. Problem: PHS projekte sehr individuell (sinnvollere annahme schwierig zu treffen)
9.  Transmission line extensions (HVDC Links)
10.  Marginal generation prices change

In [40]:
# Create networks out of old network for 2025 and 2030

# n_200 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_200_ec_lcopt_1H-noex.nc")
# n_200_optim = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\solved\elec_s300_200_ec_lcopt_1H-noex.nc")
# n_200_links = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_200_ec_lcopt_1H-noex_2030links.nc")

import pypsa
import matplotlib.pyplot as plt
import math
import pandas as pd
import gc
import numpy as np
import pickle as pkl
import glob


def set_parameters_from_optimized(network, network_optim, ratio_wind, ratio_pv):
    '''
    Function to set optimized parameters from optimized network as nominal parameters
    of the operative network.

    CHANGE IN FUNCTION: wind power allocation esp. in the north was VERY weird. Therefore: Setting p_nom of wind generators
    to p_nom and NOT p_nom_opt
    -----
    Param:
    n: Optimized investment network.
    n_optim: Operative network for redispatch simulation.
    '''
    n = network.copy()
    n_optim = network_optim.copy()

    # set line capacities to optimized
    n.lines['s_nom_extendable'] = False

    # correct incorrect line capacities
    cap_ac_type_i = 0.635
    line_typed_i = n.lines.index[n.lines.type != '']
    correction_factor = math.sqrt(3)*cap_ac_type_i
    l_shedding = abs(n_optim.lines_t.mu_upper.mean(axis=0).round(2)).nlargest(2).index.to_list()
    n.lines.loc[line_typed_i, "s_nom"] = n.lines["s_nom"] * correction_factor
    n.lines.loc[l_shedding, "s_max_pu"] = 0.7 * 1/0.66
    n.lines.loc[l_shedding, "num_parallel"] = 1

    # set link capacities to optimized (HVDC links as well as store out/inflow links)
    if not n.links.empty:
        n.links.loc['p_nom_extendable'] = False

    # set extendable generators to optimized and p_nom_extendable to False
    gen_extend_i = n.generators.index[n.generators.p_nom_extendable]

    # Overwrite renewables with un-optimized capacities to approximate real life better
    gen_onwind = n.generators.index[n.generators.carrier == "onwind"]
    gen_offwind = n.generators.index[(n.generators.carrier == "offwind-ac") | (n.generators.carrier == "offwind-dc")]
    gen_solar = n.generators.index[n.generators.carrier == "solar"]

    # correct incorrect wind data:
    n.generators.loc[gen_onwind, 'p_nom'] = n.generators['p_nom'].reindex(gen_onwind, fill_value=0.) * ratio_wind + 0.01
    n.generators.loc[(n.generators["carrier"] == "onwind")&(n.generators["p_nom"] < 200), "p_nom"] = n.generators.p_nom + 50
    #display(n.generators.loc[(n.generators["carrier"] == "onwind"), "p_nom"])

    n.generators.loc[gen_offwind, 'p_nom'] = n.generators['p_nom_max'].reindex(gen_offwind, fill_value=0.) * 0.05 + 0.01
    n.generators.loc[gen_solar, 'p_nom'] = n.generators['p_nom'].reindex(gen_solar, fill_value=0.) * ratio_pv + 0.01
    n.generators.loc[gen_extend_i, 'p_nom_extendable'] = False

    # set extendable storage unit power to ooptimized
    n.storage_units['p_nom_extendable'] = False
    # start SOC of storage_units equals state of charge at last snapshot of previous day
    n.storage_units["cyclic_state_of_charge"] = True

    return n

# Methodology: Iteratively remove rows until desired capacity reached
def remove_generator_until_capacity_reached(network, network_optim, cap_goal, carrier):
    """
    Heuristik:
    Function that removes the LEAST USED generators of a carrier until desired 
    capacity is reached (with 5% inaccuracy margin). This is done by ranking the generators by their mean utilization (loading)
    from the optimized input network.
    Param:
    cap_goal: Desired installed generator capacity
    """
    gen_names = network.generators[network.generators["carrier"] == carrier].index.tolist()
    s_gen_p_nom = network.generators[network.generators["carrier"] == carrier].p_nom

    df_gen_t = network_optim.generators_t.p[gen_names].append(s_gen_p_nom)
    s_utilization = (df_gen_t/df_gen_t.iloc[-1]).iloc[:-1].mean(axis=0)
    l_gen_remove = []

    df_gen = network.generators[network.generators["carrier"] == carrier]
    df_gen["utilization"] = s_utilization
    df_gen = df_gen.sort_values(by=["utilization"])
    for gen, next_gen in zip(df_gen.index, df_gen.index[1:]):
        # if sum of remaing generators fulfils desired capacity, remove current generator
        if df_gen["p_nom"].loc[next_gen:].sum() > cap_goal:
            l_gen_remove.append(gen)
    network.mremove("Generator", l_gen_remove)
    # display(network.generators[network.generators["carrier"] == carrier])
    return network


def build_future_network(year=2025, filename="elec_s300_220_ec_lcopt_1H-noex_2025"):
    """
    Function to build the capacities of 2025 and 2030 network from network with 2025 lines or 2030 lines & links.
    
    Assumption: Taking in to account scenario B from Netzentwicklungsplan.
    Network needs to be solved first for least utilized generator identification.
    """
    
    folder = r'C:\Users\Willem\pypsa-eur\networks_redispatch'
    filename = filename
    if year == 2025:
        subfolder = "\\2025 lines\\"
    elif year == 2030:
        subfolder = "\\2030 links\\"
    path_n = folder + subfolder + filename + ".nc"
    path_n_optim = folder + "\\solved" + subfolder + filename + ".nc"

    # Define network and network_optim
    n = pypsa.Network(path_n)
    n_optim = pypsa.Network(path_n_optim)
    network = n.copy()
    network_optim = n_optim.copy()
    
    # build post-optimized base network with additional lines (and links)
    n_future = set_parameters_from_optimized(network, network_optim, ratio_wind = 2.2, ratio_pv=1.38)
    
    # 1. Adjust load curves
    # ---------------------
    load_2018 = network.loads_t.p_set.sum(axis=1).sum()
    # From NDP:
    load_2025 = 528400000
    load_2030 = 543900000
    if year == 2025:
        ratio_load = load_2025/load_2018
    elif year == 2030:
        ratio_load = load_2030/load_2018
    
    # Scale load curves accordingly
    # Proportional scaling: Why is this ok? It increases the loads at every point in time by x%. This is ok because it implicitely
    # accounts for demo/geographic change (cities getting bigger, loads grow faster & larger than loads in villages)
    n_future.loads_t.p_set = network.loads_t.p_set.copy() * ratio_load
    
    # Map generation capacities from NDP for 2025,2030
    # ------------------------------------------------
    # Conventionals
    c_coal, c_coal2025, c_coal2030 = 25000, 13500, 9800
    c_lignite,c_lignite2025,c_lignite2030 = 21200, 9400, 9300
    c_gas,c_gas2025,c_gas2030 = 29600, 32500, 35200
    c_oil, c_oil2025, c_oil2030 = 4400, 1300, 1200
    # PHES
    c_phs, c_phs2025, c_phs2030 = 9500, 11600, 11600
    # Renewable
    c_onwind, c_onwind2025,c_onwind2030 = 50500,70500,81500
    c_offwind,c_offwind2025,c_offwind2030 = 4300,10800, 17000
    c_biomass,c_biomass2025,c_biomass2030 = 7600, 7300,6000
    c_solar,c_solar2025,c_solar2030 = 42400,73300,91300
    
    # 2. Nuclear fade out
    # ---------------------
    # remove nuclear generators from network
    n_future.mremove("Generator", n_future.generators[n_future.generators["carrier"] == "nuclear"].index)
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())    

    # 3. Coal and lignite fade out
    # --------------------------
    # Adjust installed coal and lignite capacity to 2025 or 2030
    
    if year == 2025:
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_coal2025, "coal")
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_lignite2025, "lignite")
    elif year == 2030:
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_coal2030, "coal")
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_lignite2030, "lignite")
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())    
    
    # 4. Wind power extension
    # -----------------------
    # Methodology: Add a 100 MW wind generator at every bus where wind power is below 100*2 MW (to even out the distribution)
    # 150 MW

    # onwind extension    
    n_future.generators.loc[(n_future.generators["carrier"] == "onwind")&(n_future.generators["p_nom"] < 200), "p_nom"] = \
        n_future.generators.loc[(n_future.generators["carrier"] == "onwind")&(n_future.generators["p_nom"] < 200), "p_nom"] + 100

    c_onwind_from_network = n_future.generators[network.generators["carrier"] == "onwind"].p_nom.sum()
    display(c_onwind_from_network)
    
    if year == 2025:
        n_future.generators.loc[network.generators["carrier"] == "onwind", "p_nom"] = \
            n_future.generators.p_nom * c_onwind2025 / c_onwind_from_network
    elif year == 2030:
        n_future.generators.loc[network.generators["carrier"] == "onwind", "p_nom"] = \
            n_future.generators.p_nom * c_onwind2030 / c_onwind_from_network
    
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())    


    # offwind extension
    c_offwind_from_network = n_future.generators[(n_future.generators["carrier"] == "offwind-ac")|
                                               (network.generators["carrier"] == "offwind-dc")].p_nom.sum()
    if year == 2025:
        n_future.generators.loc[network.generators["carrier"].str.contains("offwind"), "p_nom"] = \
            n_future.generators.p_nom * c_offwind2025 / c_offwind_from_network
    elif year == 2030:
        n_future.generators.loc[network.generators["carrier"].str.contains("offwind"), "p_nom"] = \
            n_future.generators.p_nom * c_offwind2030 / c_offwind_from_network

     
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())  
    
    # 5. Solar power extension
    # ------------------------
    c_solar_from_network = n_future.generators[network.generators["carrier"] == "solar"].p_nom.sum()
    display(c_solar_from_network)
    if year == 2025:
        n_future.generators.loc[network.generators["carrier"] == "solar", "p_nom"] = \
            n_future.generators.p_nom * c_solar2025 / c_solar_from_network
    elif year == 2030:
        n_future.generators.loc[network.generators["carrier"] == "solar", "p_nom"] = \
            n_future.generators.p_nom * c_solar2030 / c_solar_from_network
        
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum()) 
    
    # 6. Natural gas extention & oil reduction
    # ----------------------------------------

    # shift from oil generators to gas generators
    # Method: Existing oil generators are being removed according to "remove_generator_until_capacity_reached" rule,
    # existing gas generators are extended in 2 steps:
    #1. add 25 MW gas generator where gas capacity is lower than 25 MW
    #2. proportionally according to the ratio of ndp 2017 to ndp 2030

    # Adjust installed oil capacity to 2025 or 2030
    if year == 2025:
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_oil2025, "oil")
    elif year == 2030:
        n_future = remove_generator_until_capacity_reached(n_future, network_optim, c_oil2030, "oil")
        
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum()) 
    
    # Extend existing gas capacities
    n_future.generators.loc[((n_future.generators["carrier"] == "CCGT")|(network.generators["carrier"] == "OCGT"))
                            &(n_future.generators["p_nom"] < 25), "p_nom"] = \
                                                    n_future.generators.p_nom + 25
    
    df_gen_gas = n_future.generators[(n_future.generators["carrier"] == "CCGT")|(network.generators["carrier"] == "OCGT")]
    c_gas_from_network = df_gen_gas.p_nom.sum()
    display(c_gas_from_network)
    if year == 2025:
        n_future.generators.loc[(n_future.generators["carrier"] == "CCGT")|(network.generators["carrier"] == "OCGT"), "p_nom"] = \
            n_future.generators.p_nom * c_gas2025 / c_gas_from_network
    elif year == 2030:
        n_future.generators.loc[(n_future.generators["carrier"] == "CCGT")|(network.generators["carrier"] == "OCGT"), "p_nom"] = \
            n_future.generators.p_nom * c_gas2030 / c_gas_from_network

    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())
    
    # 7. Biomass extension
    # ----------------------
    # Methodology: multiply p_nom capacities with the ratio between Network 2018 and 2030. 

    c_biomass_from_network = n_future.generators[network.generators["carrier"] == "biomass"].p_nom.sum()
    display(c_biomass_from_network)
    if year == 2025:    
        n_future.generators.loc[network.generators["carrier"] == "biomass", "p_nom"] = \
            n_future.generators.p_nom * c_biomass2025 / c_biomass_from_network
    elif year == 2030:
        n_future.generators.loc[network.generators["carrier"] == "biomass", "p_nom"] = \
            n_future.generators.p_nom * c_biomass2030 / c_biomass_from_network
    display(n_future.generators.groupby("carrier").p_nom.sum())
    display(n_future.generators.groupby("carrier").p_nom.sum().sum())
    print("test")
    
    # 8. PHS extension
    # --------------------------

    # Waldeck extension: Waldeck bus for some reason is doubled in the bus dataframe, so looking for that bus gives the index
    coordinates_waldeck = (9.053061, 51.168410)
    buses_PHS = n_future.storage_units.bus.to_list()
    df_buses_phs = n_future.buses.loc[buses_PHS].sort_values("y")
    bus_waldeck = df_buses_phs[df_buses_phs.duplicated(["x","y"])].index[0]
    display(bus_waldeck)
    
    # -> target actual today capacity: 623 MW + 300 MW extension
    # extension: 300 MW https://web.archive.org/web/20120708055151/http://www.eon.com/de/presse/news/pressemitteilungen/2011/12/21/e-dot-on-erhaelt-genehmigung-zum-ausbau-des-pumpspeicherkraftwerks-waldeck-2.html
    n_future.storage_units.loc[str(bus_waldeck + " PHS")]["p_nom"] = 623 + 300

    # rest of the desired extension: distributed proportionally
    c_phs_from_network = n_future.storage_units["p_nom"].sum()
    if year == 2025:        
        ratio_phs = (c_phs2025 - (623 + 300))/c_phs_from_network
    elif year == 2030:        
        ratio_phs = (c_phs2030 - (623 + 300))/c_phs_from_network    
    
    n_future.storage_units[n_future.storage_units.index != str(bus_waldeck + " PHS")]["p_nom"] = \
        n_future.storage_units[n_future.storage_units.index != str(bus_waldeck + " PHS")]["p_nom"] * ratio_phs
    display(n_future.storage_units["p_nom"].sum())

    #### VALIDITY CHECK - WRITE IN THESIS: check whether total installed capacity represents the ratio between total capacity 2017 in NDP and total capacity 2030 in NDP
    sum_generation_future = n_future.generators.groupby("carrier").p_nom.sum().sum() + \
                            n_future.storage_units["p_nom"].sum()
    display(sum_generation_future)
    

    
    # 9. Marginal price adjustment
    # -----------------------------
    display(n_future.generators.groupby("carrier").marginal_cost.mean())
    # Marginal generation prices already incorporated in pypsa-eur for 2030, incl. 20€/tCo2 price.
    # Price for 2025 is assumed to be linearly between 2018 and 2025
    if year == 2025: 
        n_future.generators.loc[n_future.generators["carrier"]=="OCGT","marginal_cost"] = (n_future.generators.marginal_cost + 79.56)/2
        n_future.generators.loc[n_future.generators["carrier"]=="CCGT","marginal_cost"] = (n_future.generators.marginal_cost + 79.56 * 47/58)/2
        n_future.generators.loc[n_future.generators["carrier"]=="coal","marginal_cost"] = (n_future.generators.marginal_cost + 43)/2
        n_future.generators.loc[n_future.generators["carrier"]=="lignite","marginal_cost"] = (n_future.generators.marginal_cost + 26.98)/2
        n_future.generators.loc[n_future.generators["carrier"]=="nuclear","marginal_cost"] = (n_future.generators.marginal_cost + 5)/2
        n_future.generators.loc[n_future.generators["carrier"]=="oil","marginal_cost"] = (n_future.generators.marginal_cost + 118.79)/2
    
    display(n_future.generators.groupby("carrier").marginal_cost.mean())
    ## Export future network
    #export_path = folder 
    #n_future.export_to_netcdf(path=export_path + "\\"+ filename + "_future.nc", export_standard_types=False, least_significant_digit=None)
#

    
build_future_network(year=2025, filename="elec_s300_220_ec_lcopt_1H-Ep-noex_2025")



INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2025.nc has buses, carriers, generators, lines, loads, storage_units
INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2025.nc has buses, carriers, generators, lines, loads, storage_units


carrier
CCGT          18120.910000
OCGT           8044.269704
biomass         839.020000
coal          28069.379795
lignite       20833.500000
offwind-ac     1125.379769
offwind-dc     3359.069844
oil            3696.400000
onwind        50727.331371
ror            2907.579410
solar         43394.542511
Name: p_nom, dtype: float64

181117.38240508473

carrier
CCGT          18120.910000
OCGT           8044.269704
biomass         839.020000
coal          13953.316326
lignite       12121.000000
offwind-ac     1125.379769
offwind-dc     3359.069844
oil            3696.400000
onwind        50727.331371
ror            2907.579410
solar         43394.542511
Name: p_nom, dtype: float64

158288.81893535668

...

'DE0 32'

7285.92

232018.3157356777

carrier
CCGT           54.680000
OCGT           67.974359
biomass        14.957265
coal           39.362069
lignite        28.431767
offwind-ac      0.015000
offwind-dc      0.015000
oil           142.847328
onwind          0.015000
ror             0.000000
solar           0.010000
Name: marginal_cost, dtype: float64

carrier
CCGT           59.575517
OCGT           73.767179
biomass        14.957265
coal           41.181034
lignite        27.705884
offwind-ac      0.015000
offwind-dc      0.015000
oil           130.818664
onwind          0.015000
ror             0.000000
solar           0.010000
Name: marginal_cost, dtype: float64

In [41]:
build_future_network(year=2030, filename="elec_s300_220_ec_lcopt_1H-Ep-noex_2030")

INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2030.nc has buses, carriers, generators, lines, links, loads, storage_units
INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2030.nc has buses, carriers, generators, lines, links, loads, storage_units


carrier
CCGT          18120.910000
OCGT           8044.269704
biomass         839.020000
coal          28069.379795
lignite       20833.500000
offwind-ac     1125.379769
offwind-dc     3359.069844
oil            3696.400000
onwind        50827.341371
ror            2907.579410
solar         43394.552511
Name: p_nom, dtype: float64

181217.40240508475

carrier
CCGT          18120.910000
OCGT           8044.269704
biomass         839.020000
coal          10204.500797
lignite       12121.000000
offwind-ac     1125.379769
offwind-dc     3359.069844
oil            3696.400000
onwind        50827.341371
ror            2907.579410
solar         43394.552511
Name: p_nom, dtype: float64

154640.02340717264

...

'DE0 40'

7285.92

264742.6002074936

carrier
CCGT           54.680000
OCGT           67.974359
biomass        14.957265
coal           39.362069
lignite        28.431767
offwind-ac      0.015000
offwind-dc      0.015000
oil           142.847328
onwind          0.015000
ror             0.000000
solar           0.010000
Name: marginal_cost, dtype: float64

carrier
CCGT           54.680000
OCGT           67.974359
biomass        14.957265
coal           39.362069
lignite        28.431767
offwind-ac      0.015000
offwind-dc      0.015000
oil           142.847328
onwind          0.015000
ror             0.000000
solar           0.010000
Name: marginal_cost, dtype: float64

In [6]:
#
# Check wheather 218 networks were built correctly
#

# n_230 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_230_ec_lcopt_1H-noex.nc")
n_220 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_220_ec_lcopt_1H-noex.nc")
# n_210 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_210_ec_lcopt_1H-noex.nc")
# n_200 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_200_ec_lcopt_1H-noex.nc")
# n_190 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_190_ec_lcopt_1H-noex.nc")
# n_180 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_180_ec_lcopt_1H-noex.nc")
# n_170 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_170_ec_lcopt_1H-noex.nc")
# n_160 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_160_ec_lcopt_1H-noex.nc")
# n_150 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_150_ec_lcopt_1H-noex.nc")
# n_140 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_140_ec_lcopt_1H-noex.nc")
# n_130 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_130_ec_lcopt_1H-noex.nc")
# n_120 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_120_ec_lcopt_1H-noex.nc")
# n_110 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_110_ec_lcopt_1H-noex.nc")
# n_100 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_100_ec_lcopt_1H-noex.nc")
# n_50 =  pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_50_ec_lcopt_1H-noex.nc")
# n_10 =  pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\elec_s300_10_ec_lcopt_1H-noex.nc")



# display(n_230.generators.groupby("carrier").sum())
display(n_220.generators.groupby("carrier").sum())
# display(n_210.generators.groupby("carrier").sum())
# display(n_200.generators.groupby("carrier").sum())
# display(n_190.generators.groupby("carrier").sum())
# display(n_180.generators.groupby("carrier").sum())
# display(n_170.generators.groupby("carrier").sum())
# display(n_160.generators.groupby("carrier").sum())
# display(n_150.generators.groupby("carrier").sum())
# display(n_140.generators.groupby("carrier").sum())
# display(n_130.generators.groupby("carrier").sum())
# display(n_120.generators.groupby("carrier").sum())
# display(n_110.generators.groupby("carrier").sum())
# display(n_100.generators.groupby("carrier").sum())
# display(n_50.generators.groupby("carrier").sum())
# display(n_10.generators.groupby("carrier").sum())


# display(n_230.links)
display(n_220.links)
# display(n_210.links)
# display(n_200.links)
# display(n_190.links)
# display(n_180.links)
# display(n_170.links)
# display(n_160.links)
# display(n_150.links)
# display(n_140.links)
# display(n_130.links)
# display(n_120.links)
# display(n_110.links)
# display(n_100.links)
# display(n_50 .links)
# display(n_10 .links)


# display(n_230.lines)
display(n_220.lines)
# display(n_210.lines)
# display(n_200.lines)
# display(n_190.lines)
# display(n_180.lines)
# display(n_170.lines)
# display(n_160.lines)
# display(n_150.lines)
# display(n_140.lines)
# display(n_130.lines)
# display(n_120.lines)
# display(n_110.lines)
# display(n_100.lines)
# display(n_50 .lines)
# display(n_10 .lines)

display(n_220.lines.s_nom.sum())

#
# yes! built correctly
#

INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-noex.nc has buses, carriers, generators, lines, loads, storage_units


p_nom_max        weight         p_nom  capital_cost  \
carrier                                                              
CCGT                 inf      0.000000  18120.910000  0.000000e+00   
OCGT                 inf      0.000000   8044.269704  0.000000e+00   
biomass              inf      0.000000    839.020000  0.000000e+00   
coal                 inf      0.000000  28069.379795  0.000000e+00   
lignite              inf      0.000000  20833.500000  0.000000e+00   
nuclear              inf      0.000000  15788.438693  0.000000e+00   
offwind-ac  2.250560e+04   8396.251642     16.100000  2.041390e+06   
offwind-dc  6.718060e+04  32355.226944      0.000000  9.240328e+05   
oil                  inf      0.000000   3696.400000  0.000000e+00   
onwind      4.460423e+05  82284.135389  19897.836987  2.251489e+07   
ror                  inf   2907.579410   2907.579410  3.142912e+07   
solar       3.604510e+05  41016.216281  31443.798921  1.139826e+07   

            marginal_cost  p_nom_extendable  efficiency  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT          2407.200000                 0      25.500        0.0        0.0   
OCGT          4437.230769                 0      29.640        0.0        0.0   
biomass        463.675214                 0      14.508        0.0        0.0   
coal          1108.758621                 0      21.344        0.0        0.0   
lignite        229.290828                 0       7.599        0.0        0.0   
nuclear        185.922849                 0       3.707        0.0        0.0   
offwind-ac       0.150000                10      10.000        0.0        0.0   
offwind-dc       0.060000                 4       4.000        0.0        0.0   
oil           2995.208651                 0       9.039        0.0        0.0   
onwind           3.090000               206     206.000        0.0        0.0   
ror              0.000000                 0     104.400        0.0        0.0   
solar            2.070000               207     207.000        0.0        0.0   

            p_min_pu  p_max_pu  p_set  q_set   sign  committable  \
carrier                                                            
CCGT             0.0      51.0    0.0    0.0   51.0            0   
OCGT             0.0      76.0    0.0    0.0   76.0            0   
biomass          0.0      31.0    0.0    0.0   31.0            0   
coal             0.0      46.0    0.0    0.0   46.0            0   
lignite          0.0      17.0    0.0    0.0   17.0            0   
nuclear          0.0      11.0    0.0    0.0   11.0            0   
offwind-ac       0.0      10.0    0.0    0.0   10.0            0   
offwind-dc       0.0       4.0    0.0    0.0    4.0            0   
oil              0.0      23.0    0.0    0.0   23.0            0   
onwind           0.0     206.0    0.0    0.0  206.0            0   
ror              0.0     116.0    0.0    0.0  116.0            0   
solar            0.0     207.0    0.0    0.0  207.0            0   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0 

Empty DataFrame
Columns: [bus0, bus1, type, efficiency, p_nom, p_nom_extendable, p_nom_min, p_nom_max, p_set, p_min_pu, p_max_pu, capital_cost, marginal_cost, length, terrain_factor, p_nom_opt]
Index: []

bus0     bus1  num_parallel     length                         type  \
name                                                                          
1      DE0 0  DE0 107       2.00000  23.545620  Al/St 240/40 4-bundle 380.0   
2      DE0 0  DE0 133       0.67036  26.144454  Al/St 240/40 4-bundle 380.0   
3      DE0 0  DE0 135       3.67036  25.411087  Al/St 240/40 4-bundle 380.0   
4      DE0 0  DE0 195       2.00000  13.292403  Al/St 240/40 4-bundle 380.0   
5      DE0 0  DE0 212       2.00000  28.754420  Al/St 240/40 4-bundle 380.0   
...      ...      ...           ...        ...                          ...   
307   DE0 74   DE0 92       2.00000  86.986619  Al/St 240/40 4-bundle 380.0   
308   DE0 78   DE0 82       1.00000  82.306297  Al/St 240/40 4-bundle 380.0   
309   DE0 79   DE0 98       2.00000  20.069976  Al/St 240/40 4-bundle 380.0   
310   DE0 82   DE0 88       2.00000  45.470717  Al/St 240/40 4-bundle 380.0   
311   DE0 83    DE0 9       2.00000  47.564024  Al/St 240/40 4-bundle 380.0   

      s_max_pu        s_nom  capital_cost    s_nom_min    x    r    g    b  \
name                                                                         
1          0.7  3396.205223    894.819619  3396.205223  0.0  0.0  0.0  0.0   
2          0.7  1138.340255    993.584836  1138.340255  0.0  0.0  0.0  0.0   
3          0.7  6232.648090    965.714184  6232.648090  0.0  0.0  0.0  0.0   
4          0.7  3396.205223    505.159921  3396.205223  0.0  0.0  0.0  0.0   
5          0.7  3396.205223   1092.773078  3396.205223  0.0  0.0  0.0  0.0   
...        ...          ...           ...          ...  ...  ...  ...  ...   
307        0.7  3396.205223   3305.809516  3396.205223  0.0  0.0  0.0  0.0   
308        0.7  1698.102612   3127.940172  1698.102612  0.0  0.0  0.0  0.0   
309        0.7  3396.205223    762.732449  3396.205223  0.0  0.0  0.0  0.0   
310        0.7  3396.205223   1728.053468  3396.205223  0.0  0.0  0.0  0.0   
311        0.7  3396.205223   1807.606794  3396.205223  0.0  0.0  0.0  0.0   

      s_nom_extendable  s_nom_max  terrain_factor  v_ang_min  v_ang_max  \
name                                                                      
1                False        inf             1.0       -inf        inf   
2                False        inf             1.0       -inf        inf   
3                False        inf             1.0       -inf        inf   
4                False        inf             1.0       -inf        inf   
5                False        inf             1.0       -inf        inf   
...                ...        ...             ...        ...        ...   
307              False        inf             1.0       -inf        inf   
308              False        inf             1.0       -inf        inf   
309              False        inf             1.0       -inf        inf   
310              False        inf             1.0       -inf        inf   
311              False        inf             1.0       -inf        inf   

     sub_network  x_pu  r_pu  g_pu  b_pu  x_pu_eff  r_pu_eff  s_nom_opt  
name                                                                     
1                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
2                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
3                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
4                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
5                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
...          ...   ...   ...   ...   ...       ...       ...        ...  
307                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
308                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
309                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
310                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
311                0.0   0.0   0.0   0.0       0.0       0.0        0.0  

[311 rows x 26 columns]

1064705.6336759597

In [16]:
#
# Check wheather 2030 networks were built correctly
#
n_220_25 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\2030 links\elec_s300_220_ec_lcopt_1H-Ep-noex_2030.nc")

display(n_220_25.generators.groupby("carrier").sum())

display(n_220_25.generators.groupby("carrier").mean())

display(n_220_25.links)

display(n_220_25.lines)

display(n_220_25.lines.s_nom.sum())
#
# test done, links and lines are there.
#

INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2030.nc has buses, carriers, generators, lines, links, loads, storage_units


p_nom_max        weight         p_nom  capital_cost  \
carrier                                                              
CCGT                 inf      0.000000  18120.910000  0.000000e+00   
OCGT                 inf      0.000000   8044.269704  0.000000e+00   
biomass              inf      0.000000    839.020000  0.000000e+00   
coal                 inf      0.000000  28069.379795  0.000000e+00   
lignite              inf      0.000000  20833.500000  0.000000e+00   
nuclear              inf      0.000000  15788.438693  0.000000e+00   
offwind-ac  2.250560e+04   8396.251642     16.100000  2.041390e+06   
offwind-dc  6.718060e+04  32355.226944      0.000000  9.240328e+05   
oil                  inf      0.000000   3696.400000  0.000000e+00   
onwind      4.499279e+05  82284.135389  19897.836987  2.295207e+07   
ror                  inf   2907.579410   2907.579410  3.224195e+07   
solar       3.604993e+05  41016.216281  31443.798921  1.161852e+07   

            p_nom_extendable  marginal_cost  efficiency  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT                       0    2843.360000      26.000        0.0        0.0   
OCGT                       0    5234.025641      30.030        0.0        0.0   
biomass                    0     463.675214      14.508        0.0        0.0   
coal                       0    1810.655172      21.344        0.0        0.0   
lignite                    0     483.340045       7.599        0.0        0.0   
nuclear                    0     185.922849       3.707        0.0        0.0   
offwind-ac                10       0.150000      10.000        0.0        0.0   
offwind-dc                 4       0.060000       4.000        0.0        0.0   
oil                        0    3142.641221       8.646        0.0        0.0   
onwind                   210       3.150000     210.000        0.0        0.0   
ror                        0       0.000000     107.100        0.0        0.0   
solar                    211       2.110000     211.000        0.0        0.0   

            p_min_pu  p_max_pu  p_set  q_set   sign  committable  \
carrier                                                            
CCGT             0.0      52.0    0.0    0.0   52.0            0   
OCGT             0.0      77.0    0.0    0.0   77.0            0   
biomass          0.0      31.0    0.0    0.0   31.0            0   
coal             0.0      46.0    0.0    0.0   46.0            0   
lignite          0.0      17.0    0.0    0.0   17.0            0   
nuclear          0.0      11.0    0.0    0.0   11.0            0   
offwind-ac       0.0      10.0    0.0    0.0   10.0            0   
offwind-dc       0.0       4.0    0.0    0.0    4.0            0   
oil              0.0      22.0    0.0    0.0   22.0            0   
onwind           0.0     210.0    0.0    0.0  210.0            0   
ror              0.0     119.0    0.0    0.0  119.0            0   
solar            0.0     211.0    0.0    0.0  211.0            0   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0 

p_nom_max       weight        p_nom   capital_cost  \
carrier                                                             
CCGT                 inf     0.000000   348.479038       0.000000   
OCGT                 inf     0.000000   104.471035       0.000000   
biomass              inf     0.000000    27.065161       0.000000   
coal                 inf     0.000000   610.203909       0.000000   
lignite              inf     0.000000  1225.500000       0.000000   
nuclear              inf     0.000000  1435.312608       0.000000   
offwind-ac  2.250560e+03   839.625164     1.610000  204139.018889   
offwind-dc  1.679515e+04  8088.806736     0.000000  231008.205004   
oil                  inf     0.000000   168.018182       0.000000   
onwind      2.142514e+03   391.829216    94.751605  109295.569252   
ror                  inf    24.433440    24.433440  270940.715283   
solar       1.708527e+03   194.389651   149.022744   55064.071419   

            p_nom_extendable  marginal_cost  efficiency  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT                   False      54.680000       0.500        NaN        0.0   
OCGT                   False      67.974359       0.390        NaN        0.0   
biomass                False      14.957265       0.468        NaN        0.0   
coal                   False      39.362069       0.464        NaN        0.0   
lignite                False      28.431767       0.447        NaN        0.0   
nuclear                False      16.902077       0.337        NaN        0.0   
offwind-ac              True       0.015000       1.000        NaN        0.0   
offwind-dc              True       0.015000       1.000        NaN        0.0   
oil                    False     142.847328       0.393        NaN        0.0   
onwind                  True       0.015000       1.000        NaN        0.0   
ror                    False       0.000000       0.900        NaN        0.0   
solar                   True       0.010000       1.000        NaN        0.0   

            p_min_pu  p_max_pu  p_set  q_set  sign  committable  \
carrier                                                           
CCGT             0.0       1.0    0.0    0.0   1.0        False   
OCGT             0.0       1.0    0.0    0.0   1.0        False   
biomass          0.0       1.0    0.0    0.0   1.0        False   
coal             0.0       1.0    0.0    0.0   1.0        False   
lignite          0.0       1.0    0.0    0.0   1.0        False   
nuclear          0.0       1.0    0.0    0.0   1.0        False   
offwind-ac       0.0       1.0    0.0    0.0   1.0        False   
offwind-dc       0.0       1.0    0.0    0.0   1.0        False   
oil              0.0       1.0    0.0    0.0   1.0        False   
onwind           0.0       1.0    0.0    0.0   1.0        False   
ror              0.0       1.0    0.0    0.0   1.0        False   
solar            0.0       1.0    0.0    0.0   1.0        False   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0   
solar                 0.0

bus0     bus1 carrier  \
name                            
T10   DE0 34   DE0 72      DC   
T18   DE0 81   DE0 68      DC   
T20   DE0 46  DE0 163      DC   

                                               geometry      length   p_nom  \
name                                                                          
T10   LINESTRING (11.629014 52.252137, 12.091596 48....  603.008092  2000.0   
T18   LINESTRING (9.373979 53.922479, 9.117193 49.14...  667.806342  4000.0   
T20   LINESTRING (6.619451 51.272935, 8.458036 49.23...  337.976055   600.0   

                                                   tags  under_construction  \
name                                                                          
T10   "name"=>"HVDC SuedOstLink", "ref"=>"https://ty...                True   
T18   "name"=>"HVDC SuedLink", "ref"=>"https://tyndp...                True   
T20   "name"=>"HVDC Ultranet", "ref"=>"https://tyndp...                True   

      underground  p_min_pu  underwater_fraction  capital_cost  p_nom_min  \
name                                                                        
T10         False      -1.0             0.000000  37167.882661     2000.0   
T18         False      -1.0             0.011028  40750.019778     4000.0   
T20         False      -1.0             0.000000  27095.696411      600.0   

     type  efficiency  p_nom_extendable  p_nom_max  p_set  p_max_pu  \
name                                                                  
T10               1.0             False        inf    0.0       1.0   
T18               1.0             False        inf    0.0       1.0   
T20               1.0             False        inf    0.0       1.0   

      marginal_cost  terrain_factor  p_nom_opt  
name                                            
T10             0.0             1.0        0.0  
T18             0.0             1.0        0.0  
T20             0.0             1.0        0.0

bus0     bus1  num_parallel      length                         type  \
name                                                                           
1      DE0 0  DE0 137       2.00000   50.705225  Al/St 240/40 4-bundle 380.0   
2      DE0 0   DE0 58       2.00000   36.572250  Al/St 240/40 4-bundle 380.0   
3      DE0 1  DE0 120       1.67036   12.461968  Al/St 240/40 4-bundle 380.0   
4      DE0 1  DE0 164       0.67036   19.316323  Al/St 240/40 4-bundle 380.0   
5      DE0 1  DE0 192       0.67036   28.662694  Al/St 240/40 4-bundle 380.0   
...      ...      ...           ...         ...                          ...   
310   DE0 74    DE0 8       2.00000   99.980066  Al/St 240/40 4-bundle 380.0   
311   DE0 78   DE0 79       0.67036  168.537734  Al/St 240/40 4-bundle 380.0   
312   DE0 79    DE0 8       0.67036   67.174956  Al/St 240/40 4-bundle 380.0   
313    DE0 8   DE0 96       2.00000   47.115538  Al/St 240/40 4-bundle 380.0   
314   DE0 96   DE0 98       2.00000   84.506758  Al/St 240/40 4-bundle 380.0   

      s_max_pu        s_nom  capital_cost    s_nom_min    x    r    g    b  \
name                                                                         
1          0.7  3396.205223   1926.983907  3396.205223  0.0  0.0  0.0  0.0   
2          0.7  3396.205223   1389.879188  3396.205223  0.0  0.0  0.0  0.0   
3          0.7  2836.442867    473.600326  2836.442867  0.0  0.0  0.0  0.0   
4          0.7  1138.340255    734.090880  1138.340255  0.0  0.0  0.0  0.0   
5          0.7  1138.340255   1089.287167  1138.340255  0.0  0.0  0.0  0.0   
...        ...          ...           ...          ...  ...  ...  ...  ...   
310        0.7  3396.205223   3799.607993  3396.205223  0.0  0.0  0.0  0.0   
311        0.7  1138.340255   6405.049982  1138.340255  0.0  0.0  0.0  0.0   
312        0.7  1138.340255   2552.893906  1138.340255  0.0  0.0  0.0  0.0   
313        0.7  3396.205223   1790.562672  3396.205223  0.0  0.0  0.0  0.0   
314        0.7  3396.205223   3211.565718  3396.205223  0.0  0.0  0.0  0.0   

      s_nom_extendable  s_nom_max  terrain_factor  v_ang_min  v_ang_max  \
name                                                                      
1                False        inf             1.0       -inf        inf   
2                False        inf             1.0       -inf        inf   
3                False        inf             1.0       -inf        inf   
4                False        inf             1.0       -inf        inf   
5                False        inf             1.0       -inf        inf   
...                ...        ...             ...        ...        ...   
310              False        inf             1.0       -inf        inf   
311              False        inf             1.0       -inf        inf   
312              False        inf             1.0       -inf        inf   
313              False        inf             1.0       -inf        inf   
314              False        inf             1.0       -inf        inf   

     sub_network  x_pu  r_pu  g_pu  b_pu  x_pu_eff  r_pu_eff  s_nom_opt  
name                                                                     
1                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
2                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
3                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
4                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
5                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
...          ...   ...   ...   ...   ...       ...       ...        ...  
310                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
311                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
312                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
313                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
314                0.0   0.0   0.0   0.0       0.0       0.0        0.0  

[314 rows x 2

1093592.193616953

In [18]:
#
# Check wheather 2025 networks were built correctly
#
n_220_2025 = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks_redispatch\2025 lines\elec_s300_220_ec_lcopt_1H-Ep-noex_2025.nc")

display(n_220_2025.generators.groupby("carrier").sum())

display(n_220_25.generators.groupby("carrier").mean())

display(n_220_2025.links)

display(n_220_2025.lines)

display(n_220_2025.lines.s_nom.sum())

#
# Test done, lines work and links not there as wanted
#

INFO:pypsa.io:Imported network elec_s300_220_ec_lcopt_1H-Ep-noex_2025.nc has buses, carriers, generators, lines, loads, storage_units


p_nom_max        weight         p_nom  capital_cost  \
carrier                                                              
CCGT                 inf      0.000000  18120.910000  0.000000e+00   
OCGT                 inf      0.000000   8044.269704  0.000000e+00   
biomass              inf      0.000000    839.020000  0.000000e+00   
coal                 inf      0.000000  28069.379795  0.000000e+00   
lignite              inf      0.000000  20833.500000  0.000000e+00   
nuclear              inf      0.000000  15788.438693  0.000000e+00   
offwind-ac  2.250560e+04   8396.251642     16.100000  2.041390e+06   
offwind-dc  6.718060e+04  32355.226944      0.000000  9.240328e+05   
oil                  inf      0.000000   3696.400000  0.000000e+00   
onwind      4.466340e+05  82284.135389  19897.836987  2.284277e+07   
ror                  inf   2907.579410   2907.579410  3.197100e+07   
solar       3.604780e+05  41016.216281  31443.798921  1.156345e+07   

            efficiency  p_nom_extendable  marginal_cost  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT            25.500                 0    2788.680000        0.0        0.0   
OCGT            29.640                 0    5166.051282        0.0        0.0   
biomass         14.508                 0     463.675214        0.0        0.0   
coal            21.344                 0    1810.655172        0.0        0.0   
lignite          7.599                 0     483.340045        0.0        0.0   
nuclear          3.707                 0     185.922849        0.0        0.0   
offwind-ac      10.000                10       0.150000        0.0        0.0   
offwind-dc       4.000                 4       0.060000        0.0        0.0   
oil              9.039                 0    3285.488550        0.0        0.0   
onwind         209.000               209       3.135000        0.0        0.0   
ror            106.200                 0       0.000000        0.0        0.0   
solar          210.000               210       2.100000        0.0        0.0   

            p_min_pu  p_max_pu  p_set  q_set   sign  committable  \
carrier                                                            
CCGT             0.0      51.0    0.0    0.0   51.0            0   
OCGT             0.0      76.0    0.0    0.0   76.0            0   
biomass          0.0      31.0    0.0    0.0   31.0            0   
coal             0.0      46.0    0.0    0.0   46.0            0   
lignite          0.0      17.0    0.0    0.0   17.0            0   
nuclear          0.0      11.0    0.0    0.0   11.0            0   
offwind-ac       0.0      10.0    0.0    0.0   10.0            0   
offwind-dc       0.0       4.0    0.0    0.0    4.0            0   
oil              0.0      23.0    0.0    0.0   23.0            0   
onwind           0.0     209.0    0.0    0.0  209.0            0   
ror              0.0     118.0    0.0    0.0  118.0            0   
solar            0.0     210.0    0.0    0.0  210.0            0   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0 

p_nom_max       weight        p_nom   capital_cost  \
carrier                                                             
CCGT                 inf     0.000000   348.479038       0.000000   
OCGT                 inf     0.000000   104.471035       0.000000   
biomass              inf     0.000000    27.065161       0.000000   
coal                 inf     0.000000   610.203909       0.000000   
lignite              inf     0.000000  1225.500000       0.000000   
nuclear              inf     0.000000  1435.312608       0.000000   
offwind-ac  2.250560e+03   839.625164     1.610000  204139.018889   
offwind-dc  1.679515e+04  8088.806736     0.000000  231008.205004   
oil                  inf     0.000000   168.018182       0.000000   
onwind      2.142514e+03   391.829216    94.751605  109295.569252   
ror                  inf    24.433440    24.433440  270940.715283   
solar       1.708527e+03   194.389651   149.022744   55064.071419   

            p_nom_extendable  marginal_cost  efficiency  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT                   False      54.680000       0.500        NaN        0.0   
OCGT                   False      67.974359       0.390        NaN        0.0   
biomass                False      14.957265       0.468        NaN        0.0   
coal                   False      39.362069       0.464        NaN        0.0   
lignite                False      28.431767       0.447        NaN        0.0   
nuclear                False      16.902077       0.337        NaN        0.0   
offwind-ac              True       0.015000       1.000        NaN        0.0   
offwind-dc              True       0.015000       1.000        NaN        0.0   
oil                    False     142.847328       0.393        NaN        0.0   
onwind                  True       0.015000       1.000        NaN        0.0   
ror                    False       0.000000       0.900        NaN        0.0   
solar                   True       0.010000       1.000        NaN        0.0   

            p_min_pu  p_max_pu  p_set  q_set  sign  committable  \
carrier                                                           
CCGT             0.0       1.0    0.0    0.0   1.0        False   
OCGT             0.0       1.0    0.0    0.0   1.0        False   
biomass          0.0       1.0    0.0    0.0   1.0        False   
coal             0.0       1.0    0.0    0.0   1.0        False   
lignite          0.0       1.0    0.0    0.0   1.0        False   
nuclear          0.0       1.0    0.0    0.0   1.0        False   
offwind-ac       0.0       1.0    0.0    0.0   1.0        False   
offwind-dc       0.0       1.0    0.0    0.0   1.0        False   
oil              0.0       1.0    0.0    0.0   1.0        False   
onwind           0.0       1.0    0.0    0.0   1.0        False   
ror              0.0       1.0    0.0    0.0   1.0        False   
solar            0.0       1.0    0.0    0.0   1.0        False   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0   
solar                 0.0

Empty DataFrame
Columns: [bus0, bus1, type, efficiency, p_nom, p_nom_extendable, p_nom_min, p_nom_max, p_set, p_min_pu, p_max_pu, capital_cost, marginal_cost, length, terrain_factor, p_nom_opt]
Index: []

bus0     bus1  num_parallel     length                         type  \
name                                                                          
1      DE0 0  DE0 123       3.00000  64.430911  Al/St 240/40 4-bundle 380.0   
2      DE0 0  DE0 179       2.00000  28.300789  Al/St 240/40 4-bundle 380.0   
3      DE0 0   DE0 25       3.00000  48.025036  Al/St 240/40 4-bundle 380.0   
4      DE0 1  DE0 114       0.67036  24.174820  Al/St 240/40 4-bundle 380.0   
5      DE0 1  DE0 146       0.67036  24.253249  Al/St 240/40 4-bundle 380.0   
...      ...      ...           ...        ...                          ...   
311   DE0 66    DE0 7       0.67036  68.535305  Al/St 240/40 4-bundle 380.0   
312   DE0 71    DE0 8       3.00000  24.048678  Al/St 240/40 4-bundle 380.0   
313   DE0 76   DE0 87       3.00000  62.214496  Al/St 240/40 4-bundle 380.0   
314   DE0 78   DE0 93       2.00000  86.986619  Al/St 240/40 4-bundle 380.0   
315   DE0 84   DE0 92       1.00000  82.306297  Al/St 240/40 4-bundle 380.0   

      s_max_pu        s_nom  capital_cost    s_nom_min    x    r    g    b  \
name                                                                         
1          0.7  5094.307835   2448.610161  5094.307835  0.0  0.0  0.0  0.0   
2          0.7  3396.205223   1075.533423  3396.205223  0.0  0.0  0.0  0.0   
3          0.7  5094.307835   1825.126907  5094.307835  0.0  0.0  0.0  0.0   
4          0.7  1138.340255    918.731517  1138.340255  0.0  0.0  0.0  0.0   
5          0.7  1138.340255    921.712102  1138.340255  0.0  0.0  0.0  0.0   
...        ...          ...           ...          ...  ...  ...  ...  ...   
311        0.7  1138.340255   2604.592133  1138.340255  0.0  0.0  0.0  0.0   
312        0.7  5094.307835    913.937658  5094.307835  0.0  0.0  0.0  0.0   
313        0.7  5094.307835   2364.378264  5094.307835  0.0  0.0  0.0  0.0   
314        0.7  3396.205223   3305.809516  3396.205223  0.0  0.0  0.0  0.0   
315        0.7  1698.102612   3127.940172  1698.102612  0.0  0.0  0.0  0.0   

      s_nom_extendable  s_nom_max  terrain_factor  v_ang_min  v_ang_max  \
name                                                                      
1                False        inf             1.0       -inf        inf   
2                False        inf             1.0       -inf        inf   
3                False        inf             1.0       -inf        inf   
4                False        inf             1.0       -inf        inf   
5                False        inf             1.0       -inf        inf   
...                ...        ...             ...        ...        ...   
311              False        inf             1.0       -inf        inf   
312              False        inf             1.0       -inf        inf   
313              False        inf             1.0       -inf        inf   
314              False        inf             1.0       -inf        inf   
315              False        inf             1.0       -inf        inf   

     sub_network  x_pu  r_pu  g_pu  b_pu  x_pu_eff  r_pu_eff  s_nom_opt  
name                                                                     
1                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
2                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
3                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
4                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
5                  0.0   0.0   0.0   0.0       0.0       0.0        0.0  
...          ...   ...   ...   ...   ...       ...       ...        ...  
311                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
312                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
313                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
314                0.0   0.0   0.0   0.0       0.0       0.0        0.0  
315                0.0   0.0   0.0   0.0       0.0       0.0        0.0  

[315 rows x 26 columns]

1079428.7948248456

In [7]:
n_co2test = pypsa.Network(r"C:\Users\Willem\pypsa-eur\networks\elec_s300_5_ec_lcopt_1H-Ep-noex.nc")

display(n_co2test.generators.groupby("carrier").mean())

INFO:pypsa.io:Imported network elec_s300_5_ec_lcopt_1H-Ep-noex.nc has buses, carriers, generators, lines, loads, storage_units


p_nom_max        weight        p_nom   capital_cost  \
carrier                                                              
CCGT                 inf      0.000000  3624.182000       0.000000   
OCGT                 inf      0.000000  1608.853941       0.000000   
biomass              inf      0.000000   167.804000       0.000000   
coal                 inf      0.000000  5613.875959       0.000000   
lignite              inf      0.000000  6944.500000       0.000000   
nuclear              inf      0.000000  3947.109673       0.000000   
offwind-ac  1.125280e+04   4198.125821     8.050000  203274.624002   
offwind-dc  3.359030e+04  16177.613472     0.000000  234754.536548   
oil                  inf      0.000000   739.280000       0.000000   
onwind      8.920845e+04  16456.827078  3979.567397  109295.569252   
ror                  inf    581.515882   581.515882  270940.715283   
solar       7.209021e+04   8203.243256  6288.759784   55064.071419   

            p_nom_extendable  efficiency  marginal_cost  p_nom_opt  p_nom_min  \
carrier                                                                         
CCGT                   False       0.500      54.680000        NaN        0.0   
OCGT                   False       0.390      67.974359        NaN        0.0   
biomass                False       0.468      14.957265        NaN        0.0   
coal                   False       0.464      39.362069        NaN        0.0   
lignite                False       0.447      28.431767        NaN        0.0   
nuclear                False       0.337      16.902077        NaN        0.0   
offwind-ac              True       1.000       0.015000        NaN        0.0   
offwind-dc              True       1.000       0.015000        NaN        0.0   
oil                    False       0.393     142.847328        NaN        0.0   
onwind                  True       1.000       0.015000        NaN        0.0   
ror                    False       0.900       0.000000        NaN        0.0   
solar                   True       1.000       0.010000        NaN        0.0   

            p_min_pu  p_max_pu  p_set  q_set  sign  committable  \
carrier                                                           
CCGT             0.0       1.0    0.0    0.0   1.0        False   
OCGT             0.0       1.0    0.0    0.0   1.0        False   
biomass          0.0       1.0    0.0    0.0   1.0        False   
coal             0.0       1.0    0.0    0.0   1.0        False   
lignite          0.0       1.0    0.0    0.0   1.0        False   
nuclear          0.0       1.0    0.0    0.0   1.0        False   
offwind-ac       0.0       1.0    0.0    0.0   1.0        False   
offwind-dc       0.0       1.0    0.0    0.0   1.0        False   
oil              0.0       1.0    0.0    0.0   1.0        False   
onwind           0.0       1.0    0.0    0.0   1.0        False   
ror              0.0       1.0    0.0    0.0   1.0        False   
solar            0.0       1.0    0.0    0.0   1.0        False   

            start_up_cost  shut_down_cost  min_up_time  min_down_time  \
carrier                                                                 
CCGT                  0.0             0.0            0              0   
OCGT                  0.0             0.0            0              0   
biomass               0.0             0.0            0              0   
coal                  0.0             0.0            0              0   
lignite               0.0             0.0            0              0   
nuclear               0.0             0.0            0              0   
offwind-ac            0.0             0.0            0              0   
offwind-dc            0.0             0.0            0              0   
oil                   0.0             0.0            0              0   
onwind                0.0             0.0            0              0   
ror                   0.0             0.0            0              0   
solar      